<a href="https://colab.research.google.com/github/Cath-Strategic-Tech/adpdx_etl/blob/main/ADPDX_ClergyDB.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


# Introduction

The following notebook orchestrates the migration of ADPDX Accounts into Salesforce.



# Order of Loading

1. Vicariates
1. Organizations [MANUAL]
1. Religious Parents
1. Religious Communities
1. Religious Superiors
1. Contacts
1. Contact > Register Entries
1. Contact > Education Affiliations [MANUAL]
1. Contact > TBD
1. Affiliations


# Order of Operations

- Setup Enviro

  - [DONE] UDFs
  - [DONE] Load SF xref data

- ACCOUNTS

  - Extract Source Data
    - [DONE] Load 6 tables into separate dataframes
    - [DONE] Merge into single accounts table
    - [DONE]: Fix the ExternalID so that it references the original table, not the AccRecordType
  - Transform
    - Strip phone numbers
    - Validate email addresses
    - TODO: handle churches that aren't parishes (missions, non-diocesan parishes, etc.)
  - Load
    - [DONE]Vicariates
    - [DONE] Organizations (Parishes, Schools, Newman Centres, Offices)
    - Religious
      - [DONE] Religious Parent accounts
      - [DONE] Religious Communities
      - [DONE] Religious Superiors (Contacts, set AccountID to Rel. Parent)
        - [DONE]: Handle invalid email addresses
        - TODO: Handle duplicate entries
      - TODO: Update Religious Communities with lookup to Rel. Superior
  - TODO: Unit Tests
    - Num of Accounts, by type
    - Spot checking 3-5 account records & field values

- CONTACTS

  - Extract

    - [DONE] Import Contact records
    - TODO: Get Photo directory @soames

  - Analysis

    - [DONE] Check columns & row count (3016)
    - [DONE] Identify unique languages

  - Transform

    - Complete ETL of fields that are more complex (search for TODO)
    - [DONE] Create new df_contact_staging, renaming columns to SF APIs
    - [DONE] Drop columns that don't map to Contact
    - Migrate Languages field (waiting on next package version) @soames
      - TODO: transform `,` to `;` so imports to multi-select list correctly
    - TODO: Concat Mailing Street Address lines into one
    - TODO: Handle Private Addresses: decide if will code changes or NOT use a custom Private Address field.
    - [DONE] Update boolean fields to True/False
    - [DONE] Set Contact Record Type (UDF)
    - [DONE] Validate, drop invalid emails
    - [DONE] Generate ExternalID > 'Archdpdx_External_Id\_\_c'
    - TODO: Preferred Email/Phone > where blank, set a default. Currently, all are getting set to 'Personal' and 'Mobile.'
    - TODO: Ecclesial Status (not mapping correctly)
    - [DONE] DROP columns that haven't been mapped yet

  - Load
    - [DONE] Set JobID to curr_job_id
    - [DONE] Handle character encoding that is geting messed up

- CONTACTS > SPOUSES

- CONTACTS > PHOTOS

- CONTACTS > REGISTER ENTRIES

  - Parse columns into types of Sacraments or Notations
  - For lookups to Celebrants, query SF for contacts, create missing records
  - Generate External ID, apply to df
  - Clean up (remove extra columns, NaNs)
  - Upsert records

- CONTACTS > AFFILIATIONS

  - Map the various Contact fields that are actually Affiliations (start with manual migration)
    - Education/Degrees
    - Minor Orders
    - Religious Vows
    - Candidacy records (should this be another object?)
    - In/Excardination
    - Faculties

- AFFILIATIONS TABLE

  - Extract

    - [DONE] Turn the 'Org Table Name' & 'org Table Link' columns into External ID
    - Map in the Account IDs from SF

  - Transform

    - Parse RecordTypeId
    - Parse Category
    - Map columns to SF field APIs

  - Load


# Setup Enviro


In [3]:
# !conda install -y simple-salesforce
# !conda install -y email_validator
# !conda install -y python-dotenv

# !conda install import-ipynb


In [4]:
# enviro setup

import pandas as pd

from datetime import datetime
now = datetime.now()

from simple_salesforce import Salesforce

In [5]:
# import environment variables (SF login credentials)
from dotenv import load_dotenv
import os

load_dotenv()

True

In [6]:
# @title Global Variables { run: "auto", vertical-output: true, display-mode: "both" }

target_enviro = "adpdx_devpro" # @param {type:"string"}

# @markdown The `run_upserts` variable controls whether or not upserts to Salesforce are executed when the notebook is run.
run_upserts = "True" # @param ["True", "False"]

In [7]:
# ADPDX dev_pro credentials
adpdx_devpro_user = os.getenv('ADPDX_DEVPRO_USER')
adpdx_devpro_pass = os.getenv('ADPDX_DEVPRO_PASS')
adpdx_devpro_token = os.getenv('ADPDX_DEVPRO_TOKEN')

# instantiate a SF session object
sf = Salesforce(domain='test', username='matt+adpdx@meribahflow.com.devpro', password=adpdx_devpro_pass, security_token=adpdx_devpro_token)

## UDFs


In [8]:
# Job ID Incrementer

def update_job_id(file_name):
    # Open the file in read mode and get the current job ID
    with open(file_name, 'r') as file:
        current_job_id = int(file.readline())

    # Increment the job ID
    new_job_id = current_job_id + 1

    # Open the file in write mode and update the job ID
    with open(file_name, 'w') as file:
        file.write(str(new_job_id))

    # Return the new job ID
    return new_job_id


# Concates two DF columns for an External ID

def concat_columns(df, columns, new_column, separator='_'):
    """
    Concatenates the values from specified columns into a single string
    with the specified separator and populates a new column in the DataFrame.

    Args:
    - df: pandas DataFrame
    - columns: list of column names to concatenate
    - new_column: name of the new column to be created
    - separator: separator to use between concatenated values (default is '_')

    Returns:
    - Updated pandas DataFrame with the new column
    """
    df[new_column] = df[columns].astype(str).apply(lambda x: separator.join(x), axis=1)
    return df



from simple_salesforce import Salesforce

def get_or_create_diocesan_account(sf, account_name):
    """
    Searches for an account by name, returns the ID if found,
    otherwise creates the account with RecordType 'Church' and 'mbfc__Church_Type__c' set to 'Diocese',
    and then returns the new ID.

    Parameters:
    sf (Salesforce): Salesforce connection object
    account_name (str): The name of the account to search for or create

    Returns:
    str: The ID of the found or created account
    """

    # Query for the Record Type ID using the Developer Name 'Church'
    record_type_query = "SELECT Id FROM RecordType WHERE SobjectType = 'Account' AND DeveloperName = 'Church' LIMIT 1"
    record_type_result = sf.query(record_type_query)
    if record_type_result['records']:
        record_type_id = record_type_result['records'][0]['Id']
    else:
        raise ValueError("No RecordType found with DeveloperName 'Church'")

    # Search for the Account by name
    account_query = f"SELECT Id FROM Account WHERE Name = '{account_name}' LIMIT 1"
    account_result = sf.query(account_query)
    
    if account_result['records']:
        # Account found, return the ID
        return account_result['records'][0]['Id']
    else:
        # Account not found, create a new Account
        account_data = {
            'Name': account_name,
            'RecordTypeId': record_type_id,
            'mbfc__Church_Type__c': 'Diocese'
        }
        new_account = sf.Account.create(account_data)
        return new_account['id']




## Extract Salesforce xref data

The following cells downloads all records from the target Salesforce enviro for the following objects:

- RecordTypes
- Users
- Accounts
- Contacts


In [9]:
# Get or create the Diocesan Account and get its ID
diocesan_account_id = get_or_create_diocesan_account(sf, 'Roman Catholic Archdiocese of Portland')
print(f"Account ID: {diocesan_account_id}")

Account ID: 001Dx00001CwMTQIA3


In [10]:
# get all ACTIVE SF users

sf_users = sf.query('Select Alias, FirstName, LastName, Username, id from User WHERE IsActive = True')
df_sf_users = pd.DataFrame(sf_users['records'])
df_sf_users = df_sf_users.drop(columns = 'attributes')
df_sf_users.shape

(8, 5)

In [11]:
# get all SF Record Types
get_all_recordTypes = 'Select Id, Name, DeveloperName, sObjecttype, namespaceprefix from RecordType'

# get list of records, add to dataframe
sf_recordTypes = sf.query(get_all_recordTypes)
df_sf_recordTypes = pd.DataFrame(sf_recordTypes['records'])
df_sf_recordTypes = df_sf_recordTypes.drop(columns = 'attributes')

# Create a dictionary mapping 'DeveloperName' to 'Id' for faster lookup
record_types_mapping = df_sf_recordTypes.set_index('DeveloperName')['Id'].to_dict()

df_sf_recordTypes

Id                        Name  \
0   012Dx0000007yCpIAI                    Property   
1   012Dx0000007yIOIAY       Ecclesial Affiliation   
2   012Dx0000007yITIAY        Pastoral Assignments   
3   012Dx0000007yIYIAY                       Staff   
4   012Dx0000007yIdIAI                  Lay Person   
5   012Dx0000007yOCIAY        Diocesan Appointment   
6   012Dx0000007yOHIAY  Clergy/Religious Residence   
7   012Dx0000007yOMIAY                   Education   
8   012Dx0000007yORIAY          Ministerial Status   
9   012Dx0000007yTgIAI                z) All Types   
10  012Dx0000009TJxIAM                      Church   
11  012Dx0000009TJyIAM                     Deanery   
12  012Dx0000009TJzIAM                       Group   
13  012Dx0000009TK0IAM                   Religious   
14  012Dx0000009TK1IAM                      School   
15  012Dx0000009TK2IAM                 Consecrated   
16  012Dx0000009TK3IAM                  Lay Person   
17  012Dx0000009TK4IAM            Permanent Deacon   
18  012Dx0000009TK5IAM                      Priest   
19  012Dx0000009TK6IAM                   Religious   
20  012Dx0000009TK7IAM                       Other   
21  012Dx0000009TK8IAM              Chancery Users   
22  012Dx0000009TK9IAM               Diocean Users   
23  012Dx0000009TKAIA2          Parish Affiliation   
24  012Dx0000009TKBIA2                   Education   
25  012Dx0000009TKCIA2                  Employment   
26  012Dx0000009TKDIA2          Ministry/Volunteer   
27  012Dx0000009TKEIA2                 Parishioner   
28  012Hu000001pkqBIAQ                  Major Gift   
29  012Hu000001pkqCIAQ                       Grant   
30  012Hu000001pkqDIAQ                   Household   
31  012Hu000001pkqEIAQ                Organization   
32  012Hu000001pkqFIAQ                    Donation   
33  012Hu000001pkqGIAQ                In-Kind Gift   
34  012Hu000001pkqHIAQ               Matching Gift   
35  012Hu000001pkqIIAQ                  Membership   
36  012Hu000001pkqJIAQ                       Event   
37  012Hu000001pkqKIAQ                 Fundraising   
38  012Hu000001pkqLIAQ                     General   
39  012Hu000001pkqMIAQ                   Marketing   

                 DeveloperName           SobjectType NamespacePrefix  
0                     Property               Account            None  
1        Ecclesial_Affiliation    mbfc__Placement__c            None  
2           Assignments_Clergy    mbfc__Placement__c            None  
3                        Staff    mbfc__Placement__c            None  
4                   Lay_Person    mbfc__Placement__c            None  
5         Diocesan_Appointment    mbfc__Placement__c            None  
6   Clergy_Religious_Residence    mbfc__Placement__c            None  
7                    Education    mbfc__Placement__c            None  
8           Ministerial_Status    mbfc__Placement__c            None  
9                    All_Types    mbfc__Placement__c            None  
10                      Church               Account            mbfc  
11                     Deanery               Account            mbfc  
12                       Group               Account            mbfc  
13                   Religious               Account            mbfc  
14                      School               Account            mbfc  
15                 Consecrated               Contact            mbfc  
16                  Lay_Person               Contact            mbfc  
17            Permanent_Deacon               Contact            mbfc  
18                      Priest               Contact            mbfc  
19                   Religious               Contact            mbfc  
20                         All    mbfc__Placement__c            mbfc  
21              Chancery_Users    mbfc__Placement__c            mbfc  
22               Diocean_Users    mbfc__Placement__c            mbfc  
23                Parish_Users    mbfc__Placement__c            mbfc  
24                   Education

In [12]:
# get SF Account
get_all_accounts = 'Select id, Name, RecordTypeId, Type, mbfc__Parish_Code__c, Job_Id__c, Archdpdx_Migration_Id__c from Account'

# get list of records, add to dataframe
sf_accounts = sf.query(get_all_accounts)
df_sf_accounts = pd.DataFrame(sf_accounts['records'])
df_sf_accounts = df_sf_accounts.drop(columns = 'attributes')
df_sf_accounts.shape

(2000, 7)

In [13]:
# get SF Contacts
get_all_contacts = 'Select id, Name, npe01__Type_of_Account__c, RecordTypeId, Archdpdx_Migration_Id__c, CreatedById from Contact'

# get list of records, add to dataframe
sf_contacts = sf.query(get_all_contacts)
df_sf_contacts = pd.DataFrame(sf_contacts['records'])
df_sf_contacts = df_sf_contacts.drop(columns = 'attributes')
df_sf_contacts.shape

(2000, 6)

# ACCOUNTS


## Extract


### Load ArchdPDX csvs as DataFrames

ADPDX data for organizations is held in 6 tables, all of which will be migrated into Salesforce's Accounts object.


In [14]:
df_offices = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/Offices.csv', skiprows= lambda x: x in [1])
df_offices["src_table"] = 'Offices'
df_offices["AccountRecordType"] = 'Organization'
df_offices.rename({"Name": "Account Name"}, axis="columns", inplace=True)
df_offices.columns

Index(['Record Number', 'Common Name', 'Account Name',
       'Archdiocese Assigns Clergy', 'Locator Description', 'Mailing Address',
       'Mailing Address 2', 'Mailing Address City', 'Mailing Address State',
       'Mailing Address Province', 'Mailing Address Postal Code',
       'Mailing Address Country', 'Phone', 'Fax', 'Email', 'Web Site',
       'src_table', 'AccountRecordType'],
      dtype='object')

In [15]:
df_parishes = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/Parishes (3).csv', dtype={'Vicariate': 'object', 'Established': 'str', 'Mission Of': 'str'}, skiprows= lambda x: x in [1])
df_parishes["src_table"] = 'Parishes'
df_parishes["AccountRecordType"] = 'Church'
df_parishes.rename({"Parish Formal Name": "Account Name"}, axis="columns", inplace=True)
df_parishes.columns

Index(['Record Number', 'Common Name', 'Sort Name', 'Parish Name',
       'Account Name', 'Parish City', 'Archdiocese Assigns Clergy',
       'Mission Of', 'Established', 'Vicariate', 'Non-Latin',
       'Locator Description', 'Mailing Address', 'Mailing Address 2',
       'Mailing Address City', 'Mailing Address State',
       'Mailing Address Province', 'Mailing Address Postal Code',
       'Mailing Address Country', 'County', 'Phone', 'Fax', 'Email',
       'Web Site', 'Disabled Access', 'Sanctuary Capacity',
       'Lat/Long Coordinates Decimal', 'Google Small Embed URL',
       'Miles to Pastoral Center', 'Schedule 1 Head', 'Schedule 1 Text',
       'Schedule 2 Head', 'Schedule 2 Text', 'Schedule 3 Head',
       'Schedule 3 Text', 'Schedule 4 Head', 'Schedule 4 Text',
       'Schedule 5 Head', 'Schedule 5 Text', 'Schedule 6 Head',
       'Schedule 6 Text', 'Schedule 7 Head', 'Schedule 7 Text', 'src_table',
       'AccountRecordType'],
      dtype='object')

In [16]:
df_religious = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/RelCommunities.csv', skiprows= lambda x: x in [1])
df_religious["src_table"] = 'RelCommunities'
df_religious["AccountRecordType"] = 'Religious'
df_religious.rename({"Community Name": "Account Name"}, axis="columns", inplace=True)
df_religious.columns

Index(['Record Number', 'Common Name', 'Account Name', 'Community City',
       'Archdiocese Assigns Clergy', 'Order Full Name', 'Order Common Name',
       'Order Letters', 'Men or Women', 'Non-Latin Rite', 'Show Order in Name',
       'Description', 'Locator Description', 'Mailing Address',
       'Mailing Address 2', 'Mailing Address City', 'Mailing Address State',
       'Mailing Address Province', 'Mailing Address Postal Code',
       'Mailing Address Country', 'Phone', 'Fax', 'Email', 'Web Site',
       'Religious Order', 'Secular Order', 'Diocesan Order',
       'Pontifical Order', 'Local Superior', 'Major Superior Name',
       'Major Superior Phone', 'Major Superior Email', 'src_table',
       'AccountRecordType'],
      dtype='object')

In [17]:
df_schools = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/Schools.csv', skiprows= lambda x: x in [1])
df_schools["src_table"] = 'Schools'
df_schools["AccountRecordType"] = 'School'
df_schools.rename({"School Name": "Account Name"}, axis="columns", inplace=True)
df_schools.columns

Index(['Record Number', 'Common Name', 'Account Name', 'School City',
       'Archdiocese Assigns Clergy', 'Parish Link', 'Vicariate Link',
       'Archdiocesan School Code', 'Grades Provided', 'Established',
       'Locator Description', 'Mailing Address 1', 'Mailing Address 2',
       'Mailing Address City', 'Mailing Address State',
       'Mailing Address Province', 'Mailing Address Zip',
       'Mailing Address Country', 'Phone', 'Fax', 'Email', 'Web Site',
       'Lat/Long Coordinates Decimal', 'Google Small Embed URL', 'src_table',
       'AccountRecordType'],
      dtype='object')

In [18]:
df_vicariates = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/Vicariates.csv', skiprows= lambda x: x in [1])
df_vicariates["src_table"] = 'Vicariates'
df_vicariates["AccountRecordType"] = 'Deanery'
# As we want to designate the Common Name as what will be the Account Name in Salesforce, we are renaming these columns in a different pattern than prior CSVs.
df_vicariates.rename({"Common Name": "Account Name"}, axis="columns", inplace=True)

df_vicariates.columns

Index(['Record Number', 'Account Name', 'Vicariate Name',
       'Archdiocese Assigns Clergy', 'src_table', 'AccountRecordType'],
      dtype='object')

In [19]:
df_newman = pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/NewmanCenters.csv', skiprows= lambda x: x in [1])
df_newman["src_table"] = 'NewmanCenters'
df_newman["AccountRecordType"] = 'Organization'
df_newman.rename({"Newman Center Name": "Account Name", "Newman Center City": "Mailing Address City2"}, axis="columns", inplace=True)
df_newman.columns

Index(['Record Number', 'Common Name', 'Account Name', 'Mailing Address City2',
       'Archdiocese Assigns Clergy', 'Established', 'Locator Description',
       'Mailing Address', 'Mailing Address 2', 'Mailing Address City',
       'Mailing Address State', 'Mailing Address Province',
       'Mailing Address Postal Code', 'Mailing Address Country', 'Phone',
       'Fax', 'Email', 'Web Site', 'Lat/Long Coordinates Decimal',
       'Google Small Embed URL', 'Miles to Pastoral Center', 'Schedule 1 Head',
       'Schedule 1 Text', 'Schedule 2 Head', 'Schedule 2 Text',
       'Schedule 3 Head', 'Schedule 3 Text', 'Schedule 4 Head',
       'Schedule 4 Text', 'Schedule 5 Head', 'Schedule 5 Text',
       'Schedule 6 Head', 'Schedule 6 Text', 'Schedule 7 Head',
       'Schedule 7 Text', 'src_table', 'AccountRecordType'],
      dtype='object')

Each of the 6 tables has an overlapping but distinct set of columns, making it challenging to conform these tables into a single staging table.

In addition, columns that correspond to the same field in salesforce are named differently in each table (eg. 'Parish City' vs. 'Religious City' vs. 'Newman Center City')


In [20]:
print('TABLE: (ROWS, COLUMNS)\n')

print(f'Offices:    {df_offices.shape}')
print(f'Parishes:   {df_parishes.shape}')
print(f'Religious:  {df_religious.shape}')
print(f'Schools:    {df_schools.shape}')
print(f'Vicariates: {df_vicariates.shape}')
print(f'Newman Ctr: {df_newman.shape}')

TABLE: (ROWS, COLUMNS)

Offices:    (35, 18)
Parishes:   (151, 45)
Religious:  (70, 34)
Schools:    (56, 26)
Vicariates: (18, 6)
Newman Ctr: (4, 37)


### Merge DFs into a single Accounts DF

This step takes 6 different tables and combines them into a single Accounts table for cleaning and staging.


In [21]:
# init list of DataFrames
src_accounts = [df_offices, df_parishes, df_religious, df_schools, df_vicariates, df_newman]

# concats the various Account dataframes into one large table
accounts = pd.concat(src_accounts, ignore_index=True)

accounts.head(5)

Record Number                         Common Name  \
0              1                     Pastoral Center   
1              3                   Catholic Sentinel   
2              4                 Catholic Cemeteries   
3              6                      Griffin Center   
4             11  Providence Portland Medical Center   

                         Account Name Archdiocese Assigns Clergy  \
0                     Pastoral Center                        Yes   
1                   Catholic Sentinel                         No   
2                 Catholic Cemeteries                         No   
3                      Griffin Center                         No   
4  Providence Portland Medical Center                        Yes   

  Locator Description      Mailing Address Mailing Address 2  \
0                 NaN   2838 E Burnside St               NaN   
1                 NaN   2838 E Burnside St               NaN   
2                 NaN  333 SW Skyline Blvd               NaN   
3                 NaN   11957 SE Fuller Rd               NaN   
4                 NaN    4805 NE Glisan St               NaN   

  Mailing Address City Mailing Address State  Mailing Address Province  ...  \
0             Portland                    OR                       NaN  ...   
1             Portland                    OR                       NaN  ...   
2             Portland                    OR                       NaN  ...   
3            Milwaukie                    OR                       NaN  ...   
4             Portland                    OR                       NaN  ...   

  Major Superior Email School City Parish Link Vicariate Link  \
0                  NaN         NaN         NaN            NaN   
1                  NaN         NaN         NaN            NaN   
2                  NaN         NaN         NaN            NaN   
3                  NaN         NaN         NaN            NaN   
4                  NaN         NaN         NaN            NaN   

  Archdiocesan School Code Grades Provided Mailing Address 1  \
0                      NaN             NaN               NaN   
1                      NaN             NaN               NaN   
2                      NaN             NaN               NaN   
3                      NaN             NaN               NaN   
4                      NaN             NaN               NaN   

  Mailing Address Zip Vicariate Name Mailing Address City2  
0                 NaN            NaN                   NaN  
1                 NaN            NaN                   NaN  
2                 NaN            NaN                   NaN  
3                 NaN            NaN                   NaN  
4                 NaN            NaN                   NaN  

[5 rows x 70 columns]

## Transform


Time to do some table column renaming and re-organizing!


In [22]:
# renames columns headers to consolidate account names into SF-conformed data model
accounts.rename({"Common Name": "Name, City"}, axis="columns", inplace=True)

accounts.rename(
    columns={
        'Account Name': 'Name',
        'Mailing Address': 'BillingStreet1',
        'Mailing Address 2': 'BillingStreet2',
        'Mailing Address City': 'BillingCity',
        'Mailing Address State': 'BillingState',
        'Mailing Address Postal Code': 'BillingPostalCode',
        'Mailing Address Country': 'BillingCountry',
        'Email': 'mbfc__Email__c',
        'Web Site': 'Website',
        'Order Common Name': 'mbfc__Abbreviation__c',
        'Order Letters': 'mbfc__Religious_Suffix__c',
        'Men or Women': 'mbfc__Type_Members__c',
        'Archdiocese Assigns Clergy': 'Archdiocese_Assigns_Clergy__c',
        'Locator Description': 'Locator_Description__c',
        'Mission Of': 'Parent_Parish__c',
        'Established': 'mbfc__Date_Established__c',
        'County': 'County__c',
        'Disabled Access': 'Disabled_Access__c',
        'Sanctuary Capacity': 'Sanctuary_Capacity__c',
        'Miles to Pastoral Centre': 'Miles_to_Pastoral_Centre__c',
        'Archdiocesan School Code': 'Archdiocesan_School_Code__c',
        'Grades Provided': 'Grades_Provided__c',
    },
    inplace=True
)


# reorder column order
col = accounts.pop('Name')
accounts.insert(2, col.name, col)

col = accounts.pop('Parish Name')
accounts.insert(3, col.name, col)

col = accounts.pop('AccountRecordType')
accounts.insert(1, col.name, col)

accounts[accounts.BillingStreet2.isna() == False]

Record Number AccountRecordType  \
14              32      Organization   
32              58      Organization   
35               1            Church   
36               2            Church   
37               3            Church   
..             ...               ...   
236             62         Religious   
238             64         Religious   
239             65         Religious   
247             73         Religious   
248             74         Religious   

                                            Name, City  \
14                                    Diaconate Office   
32              Office of Marketing and Communications   
35       Our Lady of Perpetual Help, St Mary’s, Albany   
36                  St. Andrew Dũng-Lạc Mission, Aloha   
37                      St. Elizabeth Ann Seton, Aloha   
..                                                 ...   
236      Work of Jesus the High Priest, Gresham (OJSS)   
238           Heralds of the Good News, Portland (HGN)   
239  Missionary Oblates of Mary Immaculate, Rome, I...   
247           Brothers of Saint John, Laredo, TX (CSJ)   
248               Society of Mary, Washington, DC (SM)   

                                       Name Parish Name  \
14                         Diaconate Office         NaN   
32   Office of Marketing and Communications         NaN   
35    Our Lady of Perpetual Help, St Mary’s         NaN   
36                      St. Andrew Dũng-Lạc         NaN   
37                  St. Elizabeth Ann Seton         NaN   
..                                      ...         ...   
236           Work of Jesus the High Priest         NaN   
238                Heralds of the Good News         NaN   
239   Missionary Oblates of Mary Immaculate         NaN   
247                  Brothers of Saint John         NaN   
248                         Society of Mary         NaN   

    Archdiocese_Assigns_Clergy__c  \
14                            Yes   
32                            Yes   
35                            Yes   
36                             No   
37                            Yes   
..                            ...   
236                            No   
238                            No   
239                            No   
247                            No   
248                            No   

                          Locator_Description__c  \
14                                           NaN   
32                                           NaN   
35   SW Ellsworth St between 8th and 9th Streets   
36    SW Grabhorn Rd/209th Ave and Farmington Rd   
37                                           NaN   
..                                           ...   
236                                          NaN   
238                                          NaN   
239                                          NaN   
247                                          NaN   
248                                          NaN   

                                   BillingStreet1        BillingStreet2  \
14                                Pastoral Center    2838 E Burnside St   
32                                Pastoral Center    2838 E Burnside St   
35   Our Lady of Perpetual Help, St Mary’s Parish  815 Broadalbin St SW   
36                    St. Andrew Dũng-Lạc Mission   7390 SW Grabhorn Rd   
37                 St. Elizabeth Ann Seton Parish     3145 SW 192nd Ave   
..                                            ...                   ...   
236                                OJSS Community         451 NW 1st St   
238                                c/o Chancellor    2838 E Burnside St   
239         Missionary Oblates of Mary Immaculate       Via Aurelia 290   
247                               St. John Priory      505 Century Dr S   
248                 Society of Mary, USA Province      815 Varnum St NE   

    BillingCity  ...  Major Superior Email  School City Parish Link  \
14     Portland  ...                   NaN          NaN         NaN   
32   

In [23]:
# merge two Non-Latin columns into one 
accounts['Non_Latin__c'] = accounts['Non-Latin'].combine_first(accounts['Non-Latin Rite']) 

In [24]:
# export merged tables DESCRIPTION to CSV for mapping
accounts.describe(include='all').transpose().to_csv(f'/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/working/accounts.csv')
accounts.describe(include='all').transpose()

count unique                  top freq          mean  \
Record Number          334.0    NaN                  NaN  NaN          54.5   
AccountRecordType        334      5               Church  151           NaN   
Name, City               316    316      Pastoral Center    1           NaN   
Name                     334    291             St. Mary    5           NaN   
Parish Name                5      5             St. Anne    1           NaN   
...                      ...    ...                  ...  ...           ...   
Mailing Address 1         56     55  4420 SW St Marys Dr    2           NaN   
Mailing Address Zip     56.0    NaN                  NaN  NaN  97222.446429   
Vicariate Name            18     18     Albany-Corvallis    1           NaN   
Mailing Address City2      4      4            Corvallis    1           NaN   
Non_Latin__c             221      2                   No  217           NaN   

                             std      min       25%      50%      75%      max  
Record Number          41.389801      1.0     21.25     45.0    76.75    173.0  
AccountRecordType            NaN      NaN       NaN      NaN      NaN      NaN  
Name, City                   NaN      NaN       NaN      NaN      NaN      NaN  
Name                         NaN      NaN       NaN      NaN      NaN      NaN  
Parish Name                  NaN      NaN       NaN      NaN      NaN      NaN  
...                          ...      ...       ...      ...      ...      ...  
Mailing Address 1            NaN      NaN       NaN      NaN      NaN      NaN  
Mailing Address Zip     124.9586  97005.0  97134.75  97217.5  97301.0  97526.0  
Vicariate Name               NaN      NaN       NaN      NaN      NaN      NaN  
Mailing Address City2        NaN      NaN       NaN      NaN      NaN      NaN  
Non_Latin__c                 NaN      NaN       NaN      NaN      NaN      NaN  

[71 rows x 11 columns]

In [25]:
# Create a single BillingAddress field

# Concatenate the two columns with CHAR(10) as separator
accounts['BillingStreet'] = accounts[['BillingStreet1', 'BillingStreet2']].apply(lambda x: '\n'.join(x.dropna()), axis=1)

# Drop the original columns
accounts.drop(columns=['BillingStreet1', 'BillingStreet2'], inplace=True)

In [26]:
# Handle boolean fields

boolean_columns_to_convert = [
    'Archdiocese_Assigns_Clergy__c', 
    'Non_Latin__c', 
    'Disabled_Access__c', 
    ]

# Convert 'Yes'/'No' to True/False
accounts[boolean_columns_to_convert] = accounts[boolean_columns_to_convert].replace({'Yes': True, 'No': False, None: False})



In [27]:
accounts[boolean_columns_to_convert].sample(10)

Archdiocese_Assigns_Clergy__c  Non_Latin__c  Disabled_Access__c
29                           False         False               False
264                           True         False               False
60                            True         False                True
80                            True         False                True
25                            True         False               False
41                            True         False                True
122                           True         False                True
265                           True         False               False
333                          False         False               False
124                           True         False                True

In [28]:
accounts['Religious Order']

0      NaN
1      NaN
2      NaN
3      NaN
4      NaN
      ... 
329    NaN
330    NaN
331    NaN
332    NaN
333    NaN
Name: Religious Order, Length: 334, dtype: object

In [29]:
# Religious Order fields > conform to new data model

# Apply logic to create new columns
accounts['Religious_Secular_Order__c'] = accounts.apply(
    lambda x: 'Religious Order' if x['Religious Order'] == 'Yes' else ('Secular Order' if x['Secular Order'] == 'Yes' else None), axis=1
)

accounts['Pontifical_or_Diocesan_Order__c'] = accounts.apply(
    lambda x: 'Diocesan Order' if x['Diocesan Order'] == 'Yes' else ('Pontifical Order' if x['Pontifical Order'] == 'Yes' else None), axis=1
)

accounts.drop(columns=['Religious Order', 'Secular Order', 'Diocesan Order', 'Pontifical Order'], inplace=True)

In [30]:
print(accounts['mbfc__Date_Established__c'].dtype)

object


In [31]:
# Handle Date fields that are only YYYY

# Ensure all values in 'mbfc__Date_Established__c' are strings
accounts['mbfc__Date_Established__c'] = accounts['mbfc__Date_Established__c'].astype(str)

# Define a function to transform valid year values
def transform_year(year):
    if pd.notna(year) and year.replace('.', '', 1).isdigit() and len(year.split('.')[0]) == 4:
        return pd.to_datetime(year.split('.')[0] + '-01-01')
    else:
        return pd.NaT

# Apply the function to the 'mbfc__Date_Established__c' column
accounts['mbfc__Date_Established__c'] = accounts['mbfc__Date_Established__c'].apply(transform_year)


In [32]:
# Format Parent_Parish__c field

# Remove instances of '0'
accounts.Parent_Parish__c = accounts.Parent_Parish__c.str.replace('0', '')



In [33]:
# Append prefix
accounts['Parent_Parish__c'] = accounts['Parent_Parish__c'].apply(lambda x: 'Parishes_' + x if pd.notna(x) and x is not None and x != '' else x)


In [34]:
# Check final results
accounts.Parent_Parish__c[accounts.Parent_Parish__c.isna() == False].sample(10)

98                 
101                
113                
90     Parishes_141
123                
76                 
35                 
147                
62                 
80     Parishes_129
Name: Parent_Parish__c, dtype: object

In [35]:
# ParentID field

accounts['ParentId'] = accounts['Parent_Parish__c']


### AccountRecordType & ChurchType


In [36]:
#Sets all rows where AccountRecordType is Church as a Parish.
accounts.loc[accounts['AccountRecordType'] == 'Church', 'mbfc__Church_Type__c'] = 'Parish'
accounts[accounts['AccountRecordType'] == 'Church'].head(5)


Record Number AccountRecordType  \
35              1            Church   
36              2            Church   
37              3            Church   
38              4            Church   
39              5            Church   

                                       Name, City  \
35  Our Lady of Perpetual Help, St Mary’s, Albany   
36             St. Andrew Dũng-Lạc Mission, Aloha   
37                 St. Elizabeth Ann Seton, Aloha   
38     St. Peter the Fisherman Mission, Arch Cape   
39              Our Lady of the Mountain, Ashland   

                                     Name Parish Name  \
35  Our Lady of Perpetual Help, St Mary’s         NaN   
36                    St. Andrew Dũng-Lạc         NaN   
37                St. Elizabeth Ann Seton         NaN   
38                St. Peter the Fisherman         NaN   
39               Our Lady of the Mountain         NaN   

    Archdiocese_Assigns_Clergy__c  \
35                           True   
36                          False   
37                           True   
38                           True   
39                           True   

                         Locator_Description__c BillingCity BillingState  \
35  SW Ellsworth St between 8th and 9th Streets      Albany           OR   
36   SW Grabhorn Rd/209th Ave and Farmington Rd       Aloha           OR   
37                                          NaN       Aloha           OR   
38                              79441 Hwy 101 S     Seaside           OR   
39                                          NaN     Ashland           OR   

    Mailing Address Province  ... Mailing Address 1 Mailing Address Zip  \
35                       NaN  ...               NaN                 NaN   
36                       NaN  ...               NaN                 NaN   
37                       NaN  ...               NaN                 NaN   
38                       NaN  ...               NaN                 NaN   
39                       NaN  ...               NaN                 NaN   

   Vicariate Name Mailing Address City2 Non_Latin__c  \
35            NaN                   NaN        False   
36            NaN                   NaN        False   
37            NaN                   NaN        False   
38            NaN                   NaN        False   
39            NaN                   NaN        False   

                                        BillingStreet  \
35  Our Lady of Perpetual Help, St Mary’s Parish\n...   
36   St. Andrew Dũng-Lạc Mission\n7390 SW Grabhorn Rd   
37  St. Elizabeth Ann Seton Parish\n3145 SW 192nd Ave   
38         St. Peter the Fisherman Mission\nPO Box 29   
39   Our Lady of the Mountain Parish\n987 Hillview Dr   

   Religious_Secular_Order__c Pontifical_or_Diocesan_Order__c      ParentId  \
35                       None                            None                 
36                       None                            None   Parishes_83   
37                       None                            None                 
38                       None                            None  Parishes_131   
39                       None                            None                 

   mbfc__Church_Type__c  
35               Parish  
36               Parish  
37               Parish  
38               Parish  
39               Parish  

[5 rows x 70 columns]

### Generate ExternalId


In [37]:
# Generate an External ID
columns_to_concate = ['src_table', 'Record Number']
accounts = concat_columns(accounts, columns_to_concate, 'Archdpdx_Migration_Id__c', separator='_')

In [38]:
# set Deanery RecordTypeId to the Church RecordTypeId
# map in RecordTypeIds
accounts['RecordTypeId'] = accounts['AccountRecordType'].map(record_types_mapping)
record_types_mapping

{'Property': '012Dx0000007yCpIAI',
 'Ecclesial_Affiliation': '012Dx0000007yIOIAY',
 'Assignments_Clergy': '012Dx0000007yITIAY',
 'Staff': '012Dx0000007yIYIAY',
 'Lay_Person': '012Dx0000009TK3IAM',
 'Diocesan_Appointment': '012Dx0000007yOCIAY',
 'Clergy_Religious_Residence': '012Dx0000007yOHIAY',
 'Education': '012Dx0000009TKBIA2',
 'Ministerial_Status': '012Dx0000007yORIAY',
 'All_Types': '012Dx0000007yTgIAI',
 'Church': '012Dx0000009TJxIAM',
 'Deanery': '012Dx0000009TJyIAM',
 'Group': '012Dx0000009TJzIAM',
 'Religious': '012Dx0000009TK6IAM',
 'School': '012Dx0000009TK1IAM',
 'Consecrated': '012Dx0000009TK2IAM',
 'Permanent_Deacon': '012Dx0000009TK4IAM',
 'Priest': '012Dx0000009TK5IAM',
 'All': '012Dx0000009TK7IAM',
 'Chancery_Users': '012Dx0000009TK8IAM',
 'Diocean_Users': '012Dx0000009TK9IAM',
 'Parish_Users': '012Dx0000009TKAIA2',
 'Employment': '012Dx0000009TKCIA2',
 'Ministry_Volunteer': '012Dx0000009TKDIA2',
 'Parishioner': '012Dx0000009TKEIA2',
 'MajorGift': '012Hu000001pkqBIAQ'

### Send to CSV for examination

## Load


### Generate a new Job ID


In [39]:
# increment to the job_id
file_name = '/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/jobs/job_id'
curr_job_id = update_job_id(file_name)
print(f"New job ID: {curr_job_id}")

# add/update account DF with job_id
accounts["Job_Id__c"] = curr_job_id


New job ID: 82


### A) Vicariates


In [40]:
vicariates = accounts[accounts['AccountRecordType'] == 'Deanery']

vicariates = vicariates[[
    'Record Number',
    'Name',
    # 'AccountRecordType',
    'Job_Id__c',
    'Archdpdx_Migration_Id__c',
    'RecordTypeId'
    ]]

# add parentid
vicariates["mbfc__Diocese__c"] = diocesan_account_id
vicariates['ParentId'] = diocesan_account_id
vicariates['mbfc__Church_Type__c'] = 'Deanery'

vicariates.rename(columns={
        # 'Name, City': 'Name',
        'External_Id': 'Archdpdx_Migration_Id__c'
    }, inplace=True)

vicariates.reset_index()
vicariates.set_index('Record Number', inplace=True)

vicariates

Name  Job_Id__c  \
Record Number                                                  
1                      Albany-Corvallis Vicariate         82   
2                   Beaverton, Suburban Vicariate         82   
3                       Columbia County Vicariate         82   
4                     Downtown Portland Vicariate         82   
5               East Portland, Suburban Vicariate         82   
6                         Marion County Vicariate         82   
7                   Metropolitan Eugene Vicariate         82   
8                    Metropolitan Salem Vicariate         82   
9                           North Coast Vicariate         82   
10                   Northeast Portland Vicariate         82   
11                              Santiam Vicariate         82   
12                          South Coast Vicariate         82   
13             South Portland, Suburban Vicariate         82   
14                   Southeast Portland Vicariate         82   
15                      Southern Oregon Vicariate         82   
16                      Tualatin Valley Vicariate         82   
17              West Portland, Suburban Vicariate         82   
18                       Yamhill County Vicariate         82   

              Archdpdx_Migration_Id__c        RecordTypeId  \
Record Number                                                
1                         Vicariates_1  012Dx0000009TJyIAM   
2                         Vicariates_2  012Dx0000009TJyIAM   
3                         Vicariates_3  012Dx0000009TJyIAM   
4                         Vicariates_4  012Dx0000009TJyIAM   
5                         Vicariates_5  012Dx0000009TJyIAM   
6                         Vicariates_6  012Dx0000009TJyIAM   
7                         Vicariates_7  012Dx0000009TJyIAM   
8                         Vicariates_8  012Dx0000009TJyIAM   
9                         Vicariates_9  012Dx0000009TJyIAM   
10                       Vicariates_10  012Dx0000009TJyIAM   
11                       Vicariates_11  012Dx0000009TJyIAM   
12                       Vicariates_12  012Dx0000009TJyIAM   
13                       Vicariates_13  012Dx0000009TJyIAM   
14                       Vicariates_14  012Dx0000009TJyIAM   
15                       Vicariates_15  012Dx0000009TJyIAM   
16                       Vicariates_16  012Dx0000009TJyIAM   
17                       Vicariates_17  012Dx0000009TJyIAM   
18                       Vicariates_18  012Dx0000009TJyIAM   

                 mbfc__Diocese__c            ParentId mbfc__Church_Type__c  
Record Number                                                               
1              001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
2              001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
3              001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
4              001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
5              001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
6              001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
7              001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
8              001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
9              001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
10             001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
11             001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
12             001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
13             001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
14             001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
15             001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
16             001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
17             001Dx00001CwMTQIA3  001Dx00001CwMTQIA3              Deanery  
18             001Dx00001CwMTQIA3  001Dx00001CwMTQIA3       

#### Export Vicariates to CSV


In [41]:
# export to CSV
vicariates.to_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/staging/vicariates_staging.csv')


#### Upsert Vicariates


In [42]:
bulk_data = []
for row in vicariates.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

if run_upserts == 'True':
    vicariate_upsert = sf.bulk.Account.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
    upserts = pd.DataFrame(vicariate_upsert)

    print(upserts)
    

    success  created                  id errors
0      True    False  001Dx00001FaTb0IAF     []
1      True    False  001Dx00001FaTb1IAF     []
2      True    False  001Dx00001FaTb2IAF     []
3      True    False  001Dx00001FaTb3IAF     []
4      True    False  001Dx00001FaTb4IAF     []
5      True    False  001Dx00001FaTb5IAF     []
6      True    False  001Dx00001FaTb6IAF     []
7      True    False  001Dx00001FaTb7IAF     []
8      True    False  001Dx00001FaTb8IAF     []
9      True    False  001Dx00001FaTb9IAF     []
10     True    False  001Dx00001FaTbAIAV     []
11     True    False  001Dx00001FaTbBIAV     []
12     True    False  001Dx00001FaTbCIAV     []
13     True    False  001Dx00001FaTbDIAV     []
14     True    False  001Dx00001FaTbEIAV     []
15     True    False  001Dx00001FaTbFIAV     []
16     True    False  001Dx00001FaTbGIAV     []
17     True    False  001Dx00001FaTbHIAV     []


In [43]:
# Generate an Errors log
import csv

keys = vicariate_upsert[0].keys()

with open('results_files/vicariate_results', 'w', newline='') as csv_file:
    writer = csv.DictWriter(csv_file, keys)
    writer.writeheader()
    writer.writerows(vicariate_upsert)

In [44]:
# @title Get Vicariate records from SF

sf_deaneries = sf.query("SELECT Archdpdx_Migration_Id__c, Id FROM Account WHERE RecordType.DeveloperName = 'Deanery'")

df_sf_deaneries = pd.DataFrame(sf_deaneries['records'])
df_sf_deaneries = df_sf_deaneries.drop(columns = 'attributes')

df_sf_deaneries

# Creates a dict of Vicariate unique ids to the new Salesforce record IDs, so can populate on latter Account records
vicariate_sf_recordids = df_sf_deaneries.set_index('Archdpdx_Migration_Id__c')['Id'].to_dict()
vicariate_sf_recordids

{'Vicariates_1': '001Dx00001FaTb0IAF',
 'Vicariates_2': '001Dx00001FaTb1IAF',
 'Vicariates_3': '001Dx00001FaTb2IAF',
 'Vicariates_4': '001Dx00001FaTb3IAF',
 'Vicariates_5': '001Dx00001FaTb4IAF',
 'Vicariates_6': '001Dx00001FaTb5IAF',
 'Vicariates_7': '001Dx00001FaTb6IAF',
 'Vicariates_8': '001Dx00001FaTb7IAF',
 'Vicariates_9': '001Dx00001FaTb8IAF',
 'Vicariates_10': '001Dx00001FaTb9IAF',
 'Vicariates_11': '001Dx00001FaTbAIAV',
 'Vicariates_12': '001Dx00001FaTbBIAV',
 'Vicariates_13': '001Dx00001FaTbCIAV',
 'Vicariates_14': '001Dx00001FaTbDIAV',
 'Vicariates_15': '001Dx00001FaTbEIAV',
 'Vicariates_16': '001Dx00001FaTbFIAV',
 'Vicariates_17': '001Dx00001FaTbGIAV',
 'Vicariates_18': '001Dx00001FaTbHIAV'}

### B) Parishes, Schools, Organizations


In [57]:
# Create acc_main (accounts excluding Deaneries (already handled) and Religious (to be handled differently, after))
acc_main = accounts[accounts['AccountRecordType'] != 'Deanery']
acc_main = acc_main[acc_main['AccountRecordType'] != 'Religious']

acc_main.loc[acc_main['AccountRecordType'] == 'Church', 'Vicariate_Ext_Id'] = 'Vicariates_' + acc_main['Vicariate']

acc_main.sample(5)

Record Number AccountRecordType  \
264             11            School   
23              41      Organization   
311             58            School   
273             20            School   
35               1            Church   

                                        Name, City  \
264                Blanchet Catholic School, Salem   
23                Santiam Correctional Institution   
311  Resurrection Catholic Parish School, Tualatin   
273                 O’Hara Catholic School, Eugene   
35   Our Lady of Perpetual Help, St Mary’s, Albany   

                                      Name Parish Name  \
264               Blanchet Catholic School         NaN   
23        Santiam Correctional Institution         NaN   
311    Resurrection Catholic Parish School         NaN   
273                 O’Hara Catholic School         NaN   
35   Our Lady of Perpetual Help, St Mary’s         NaN   

     Archdiocese_Assigns_Clergy__c  \
264                           True   
23                            True   
311                           True   
273                           True   
35                            True   

                          Locator_Description__c BillingCity BillingState  \
264                                          NaN       Salem           OR   
23                                           NaN       Salem           OR   
311                                          NaN    Tualatin           OR   
273                                          NaN      Eugene           OR   
35   SW Ellsworth St between 8th and 9th Streets      Albany           OR   

     Mailing Address Province  ... Non_Latin__c  \
264                       NaN  ...        False   
23                        NaN  ...        False   
311                       NaN  ...        False   
273                       NaN  ...        False   
35                        NaN  ...        False   

                                         BillingStreet  \
264                                                      
23                               4005 Aumsville Hwy SE   
311                                                      
273                                                      
35   Our Lady of Perpetual Help, St Mary’s Parish\n...   

    Religious_Secular_Order__c Pontifical_or_Diocesan_Order__c ParentId  \
264                       None                            None      NaN   
23                        None                            None      NaN   
311                       None                            None      NaN   
273                       None                            None      NaN   
35                        None                            None            

    mbfc__Church_Type__c Archdpdx_Migration_Id__c        RecordTypeId  \
264                  NaN               Schools_11  012Dx0000009TK1IAM   
23                   NaN               Offices_41  012Hu000001pkqEIAQ   
311                  NaN               Schools_58  012Dx0000009TK1IAM   
273                  NaN               Schools_20  012Dx0000009TK1IAM   
35                Parish               Parishes_1  012Dx0000009TJxIAM   

    Job_Id__c Vicariate_Ext_Id  
264        82              NaN  
23         82              NaN  
311        82              NaN  
273        82              NaN  
35         82     Vicariates_1  

[5 rows x 74 columns]

In [58]:
# map in Deaneries
acc_main['mbfc__Deanery__c'] = acc_main.Vicariate_Ext_Id.map(vicariate_sf_recordids)

acc_main[acc_main['AccountRecordType'] == 'Church']['mbfc__Deanery__c']

35     001Dx00001FaTb0IAF
36     001Dx00001FaTbCIAV
37     001Dx00001FaTbFIAV
38     001Dx00001FaTb8IAF
39     001Dx00001FaTbEIAV
              ...        
181    001Dx00001FaTb4IAF
182    001Dx00001FaTbGIAV
183    001Dx00001FaTb5IAF
184    001Dx00001FaTbHIAV
185    001Dx00001FaTb6IAF
Name: mbfc__Deanery__c, Length: 151, dtype: object

In [59]:
# Clean up NaN values

acc_main.fillna('', inplace=True)

In [62]:
# Generate final Schedule text from all Schedule columns

def create_account_schedule(row):
    account_schedule = []
    for i in range(1, 8):
        head_col = f'Schedule {i} Head'
        text_col = f'Schedule {i} Text'
        
        head = row[head_col]
        text = row[text_col]
        
        if pd.notnull(head) or pd.notnull(text):
            if pd.notnull(head):
                account_schedule.append(f"<p><strong>{head}</strong></p>")
            if pd.notnull(text):
                account_schedule.append(f"<p>{text}</p>")
            account_schedule.append("<p><br></p>")
    
    # Join all parts into a single string
    return "".join(account_schedule).strip()

acc_main['Account_Schedule__c'] = acc_main.apply(create_account_schedule, axis=1)



In [63]:
acc_main['Account_Schedule__c'].sample(15)

23     <p><strong></strong></p><p></p><p><br></p><p><...
331    <p><strong>Weekend Mass</strong></p><p>Saturda...
267    <p><strong></strong></p><p></p><p><br></p><p><...
18     <p><strong></strong></p><p></p><p><br></p><p><...
279    <p><strong></strong></p><p></p><p><br></p><p><...
29     <p><strong></strong></p><p></p><p><br></p><p><...
31     <p><strong></strong></p><p></p><p><br></p><p><...
131    <p><strong>Weekend Mass</strong></p><p>Saturda...
296    <p><strong></strong></p><p></p><p><br></p><p><...
280    <p><strong></strong></p><p></p><p><br></p><p><...
72     <p><strong>Weekend Mass</strong></p><p>Saturda...
44     <p><strong>Weekend Mass</strong></p><p>Saturda...
73     <p><strong>Weekend Mass</strong></p><p>Saturda...
45     <p><strong>Mass</strong></p><p>Sunday 11:30 am...
47     <p><strong>Mass</strong></p><p>Sunday 11:00 am...
Name: Account_Schedule__c, dtype: object

In [64]:
# Create 'account_staging' df (drop extraneous columns)

accounts_staging = acc_main[[
    'Name',
    'RecordTypeId',
    'mbfc__Church_Type__c',
    'mbfc__Deanery__c',
    'BillingStreet',
    'BillingCity',
    'BillingState',
    'BillingPostalCode',
    'BillingCountry',
    'Phone',
    'Fax',
    'mbfc__Email__c',
    'Website',
    'Account_Schedule__c',
    'mbfc__Abbreviation__c',
    'mbfc__Religious_Suffix__c',
    'mbfc__Type_Members__c',
    'Description',
    'Archdiocese_Assigns_Clergy__c', # Boolean fields
    'Non_Latin__c', 
    'Disabled_Access__c', 
    'Locator_Description__c',
    'Parent_Parish__c',
    'mbfc__Date_Established__c',
    'County__c',
    'Sanctuary_Capacity__c',
    # 'Miles_to_Pastoral_Centre__c',
    'Religious_Secular_Order__c',
    'Pontifical_or_Diocesan_Order__c',
    'Archdiocesan_School_Code__c',
    'Grades_Provided__c',
    'Job_Id__c',
    'Archdpdx_Migration_Id__c',
    # 'ParentId'  # Later, check whether or not can upsert using external ID using this field

    ]]

In [68]:
accounts_staging['Parent_Parish__c'].sample(20)

72                 
81                 
140                
84                 
7                  
38     Parishes_131
75       Parishes_7
311                
135                
12                 
148     Parishes_42
300                
121                
55                 
76                 
141                
66                 
270                
271                
11                 
Name: Parent_Parish__c, dtype: object

In [ ]:
# send accounts_staging to csv
accounts_staging.to_csv('staging_files/accounts_staging.csv', encoding='utf-8-sig')

#### Upsert Accounts (TBD )


In [ ]:
# FIXME: Format ExternalID lookups into dictionary to match SF's api so can upsert using simple-salesforce

# Rename columns apis
accounts_staging = accounts_staging.rename(columns={'Parent_Parish__c': 'Parent_Parish__r'})  # Later on, attempt to include 'ParentId' (which, as a standard SF field, might not work)

# Reformat values to match what SF api requires
accounts_staging['Parent_Parish__r'] = accounts_staging.apply(lambda x: "{'Archdpdx_Migration_Id__c': '" + x['Parent_Parish__r'] + "'}" if pd.notna(x['Parent_Parish__r']) and x['Parent_Parish__r'] != 'None' and x['Parent_Parish__r'] != '' else None, axis=1)




In [ ]:
# send accounts_staging to csv
accounts_staging.to_csv('staging_files/accounts_staging.csv', encoding='utf-8-sig')

In [ ]:
# Remove all NaT values
accounts_staging.replace({pd.NaT: None}, inplace=True)

# convert '' to NaN
accounts_staging.replace("", np.nan, inplace=True)

# convert NaN to None
accounts_staging = df_contact_staging.where(df_contact_staging.notnull(), None)


In [ ]:
bulk_data = []
for row in accounts_staging.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

In [ ]:
# Ensure all values are JSON serializable
import json

def make_json_serializable(records):
    for record in records:
        for key, value in record.items():
            if isinstance(value, pd.Timestamp):
                record[key] = value.isoformat() if not pd.isna(value) else None
    return records

bulk_data = make_json_serializable(bulk_data)

# Ensure that records are JSON serializable
json.dumps(bulk_data)  # This line will raise an error if there's still any non-serializable value



'[{"ADPDX_Clergy_Status__c": "Transferred Out", "ADPDX_Religious_Status__c": null, "ADPDX_Login_ID__c": "sabukaka", "ADPDX_Access_Permission__c": null, "Salutation": "Rev.", "FirstName": "Stephen", "MiddleName": "Ozovehe", "LastName": "Abaukaka", "Suffix": null, "MailingStreet": "Brighton Hospice Office", "MailingCity": "Tualatin", "MailingState": "OR", "MailingPostalCode": "97062", "MailingCountry": null, "npe01__WorkPhone__c": "503-430-7699", "HomePhone": null, "MobilePhone": "773-733-3772", "npe01__WorkEmail__c": null, "npe01__AlternateEmail__c": null, "npe01__HomeEmail__c": "abstoz@yahoo.com", "Directory_Include__c": true, "Directory_Include_Middle_Name__c": false, "Directory_Include_Suffix__c": false, "Suppress_From_Reports__c": false, "adpdx_Seminarian_Student_Debt__c": "0", "adpdx_Seminarian_Medical_Benefits__c": null, "Send_Group_Mail_and_Email__c": true, "Birthdate": "1967-06-07", "mbfc__Place_of_Birth__c": null, "Foreign_Born__c": false, "Foreign_Citizenship__c": null, "Immig

In [ ]:
#FIXME: account_staging isn't upserting via simple-salesforce (but it is via the Salesforce API)
from simple_salesforce.exceptions import SalesforceMalformedRequest

if run_upserts == 'True':

    try:
        account_staging_upsert = sf.bulk.Account.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
        account_upserts = pd.DataFrame(account_staging_upsert)
    except SalesforceMalformedRequest as e:
        # If a SalesforceMalformedRequest error occurs, print the error message and response content
        print(f"SalesforceMalformedRequest error: {e}")
        print(f"Response content: {e.content}")

SalesforceMalformedRequest error: Malformed request https://adpdx--devpro.sandbox.my.salesforce.com/services/async/57.0/job/750Dx000007zmAJIAY/batch/751Dx000009HT2uIAG/result. Response content: {'exceptionCode': 'InvalidBatch', 'exceptionMessage': 'Records not processed'}
Response content: {'exceptionCode': 'InvalidBatch', 'exceptionMessage': 'Records not processed'}


In [ ]:
# Generate an Errors log
# import csv

# keys = account_staging_upsert[0].keys()

# with open('results_files/accounts_results', 'w', newline='') as csv_file:
#     writer = csv.DictWriter(csv_file, keys)
#     writer.writeheader()
#     writer.writerows(account_staging_upsert)

NameError: name 'account_staging_upsert' is not defined

In [ ]:
# @title Extract SF Account records

sf_accounts = sf.query('Select id, Name, RecordTypeId, mbfc__Church_Type__c, Archdpdx_Migration_Id__c, Job_Id__c from Account WHERE Job_Id__c != null')
sf_accounts = pd.DataFrame(sf_accounts['records'])
sf_accounts = sf_accounts.drop(columns = 'attributes')
sf_accounts

Id                                    Name  \
0    001Dx00001FZm6kIAD            St. Francis of Assisi School   
1    001Dx00001FZm6lIAD       Valley Catholic Elementary School   
2    001Dx00001FZm6mIAD           Valley Catholic Middle School   
3    001Dx00001FZm6nIAD             Valley Catholic High School   
4    001Dx00001FZm6oIAD  De La Salle North Catholic High School   
..                  ...                                     ...   
371  001Dx00001FaTbDIAV            Southeast Portland Vicariate   
372  001Dx00001FaTbEIAV               Southern Oregon Vicariate   
373  001Dx00001FaTbFIAV               Tualatin Valley Vicariate   
374  001Dx00001FaTbGIAV       West Portland, Suburban Vicariate   
375  001Dx00001FaTbHIAV                Yamhill County Vicariate   

           RecordTypeId mbfc__Church_Type__c Archdpdx_Migration_Id__c  \
0    012Hu000001pkqEIAQ                 None           Organization_5   
1    012Hu000001pkqEIAQ                 None           Organization_8   
2    012Hu000001pkqEIAQ                 None           Organization_9   
3    012Hu000001pkqEIAQ                 None          Organization_10   
4    012Hu000001pkqEIAQ                 None          Organization_13   
..                  ...                  ...                      ...   
371  012Dx0000009TJyIAM              Deanery            Vicariates_14   
372  012Dx0000009TJyIAM              Deanery            Vicariates_15   
373  012Dx0000009TJyIAM              Deanery            Vicariates_16   
374  012Dx0000009TJyIAM              Deanery            Vicariates_17   
375  012Dx0000009TJyIAM              Deanery            Vicariates_18   

    Job_Id__c  
0          36  
1          36  
2          36  
3          36  
4          36  
..        ...  
371        81  
372        81  
373        81  
374        81  
375        81  

[376 rows x 6 columns]

### C) Religious Institutes (Parents)


In [56]:
"""
- 'acc_religious' DF: create unique_id of religious parents
- create 'acc_religious_orders' DF , upsert into SF
- extract accounts from Salesforce, create dict (external_ID : account_ID)
- map parent ids onto religious child accounts DF in main DF
- 'acc_religious' > staging DF ('acc_religious')
    - drop unnecessary columns
    - upsert create DF of religious children, upsert into SF with
"""

# Create a new DF of all Religious accounts
acc_religious = accounts[accounts['AccountRecordType'] == 'Religious']

# Create a simplified external ID field
acc_religious['Archdpdx_Migration_Id__c'] = acc_religious['Order Full Name'].apply(
    lambda x: x.lower().replace(' ', '')[:40]
)

acc_religious_2 = acc_religious

# Create a DF for only parent religious order accounts
acc_religious_parents = acc_religious_2[[
    'Order Full Name', 
    'Name', 
    'mbfc__Abbreviation__c', 
    'mbfc__Religious_Suffix__c', 
    'mbfc__Type_Members__c', 
    'Archdpdx_Migration_Id__c',
    'Pontifical_or_Diocesan_Order__c',
    'Religious_Secular_Order__c',
    ]]

# Drop duplicate rows of the same parent Religious Order (becuase there are more than 1 local community of a particular order)
acc_religious_parents.drop_duplicates('Order Full Name', inplace=True)

# How many remaining rows after dropping duplicates?
print(acc_religious_parents.shape)

# Rename columns
acc_religious_parents = acc_religious_parents.rename(columns={
    'Order Full Name': 'Description'
    })

# Drop NA
acc_religious_parents.fillna('', inplace=True)

acc_religious_parents


(62, 8)


/var/folders/_g/p51k4k2d5fg45slnqjhgd3sc0000gn/T/ipykernel_24056/2548649369.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acc_religious['Archdpdx_Migration_Id__c'] = acc_religious['Order Full Name'].apply(
/var/folders/_g/p51k4k2d5fg45slnqjhgd3sc0000gn/T/ipykernel_24056/2548649369.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acc_religious_parents.drop_duplicates('Order Full Name', inplace=True)


Description  \
186                                 Societas Iesu   
187   Ordo Cisterciensis Strictioris Observantiae   
189                         Ordo Sancti Benedicti   
190                 Misioneros del Espíritu Santo   
191                             Apostles of Jesus   
..                                            ...   
249                 Fraternità san Carlo Borromeo   
250                 Sons of Mary, Mother of Mercy   
251                    Society of the Divine Word   
252                 Society of the Divine Saviour   
253  Society of Our Lady of the Most Holy Trinity   

                                                  Name  \
186                        Colombiere Jesuit Community   
187                     Abbey of Our Lady of Guadalupe   
189             Benedictine Monks of Mount Angel Abbey   
190   Missionaries of the Holy Spirit Provincial House   
191                                  Apostles of Jesus   
..                                                 ...   
249  Priestly Fraternity of the Missionaries of St....   
250                      Sons of Mary, Mother of Mercy   
251                         Society of the Divine Word   
252                      Society of the Divine Saviour   
253       Society of Our Lady of the Most Holy Trinity   

                                 mbfc__Abbreviation__c  \
186                                            Jesuits   
187                                          Trappists   
189                                       Benedictines   
190  Missionaries of the Holy Spirit, Christ the Pr...   
191                                  Apostles of Jesus   
..                                                 ...   
249                          Fraternity of St. Charles   
250                      Sons of Mary, Mother of Mercy   
251                         Society of the Divine Word   
252                      Society of the Divine Saviour   
253       Society of Our Lady of the Most Holy Trinity   

    mbfc__Religious_Suffix__c mbfc__Type_Members__c  \
186                        SJ                   Men   
187                      OCSO                   Men   
189                       OSB                   Men   
190                      MSpS                   Men   
191                        AJ                   Men   
..                        ...                   ...   
249                      FSCB                   Men   
250                      SMMM                   Men   
251                       SVD                   Men   
252                       SDS                   Men   
253                      SOLT                   Men   

                     Archdpdx_Migration_Id__c Pontifical_or_Diocesan_Order__c  \
186                              societasiesu                                   
187  ordocisterciensisstrictiorisobservantiae                Pontifical Order   
189                       ordosanctibenedicti                                   
190                misionerosdelespíritusanto                                   
191                           apostlesofjesus                  Diocesan Order   
..                                        ...                             ...   
249                fraternitàsancarloborromeo                                   
250                  sonsofmary,motherofmercy                                   
251                    societyofthedivineword                                   
252                 societyofthedivinesaviour                                   
253      societyofourladyofthemostholytrinity                                   

    Religious_Secular_Order__c  
186            Religious Order  
187            Religious Order  
189            Religious Order  
190                             
191            Religious Order  
..                         ...  
249                             
250                             
251                             
252                             
253       

In [57]:
acc_religious_parents['Religious_Type__c'] = 'Congregation'

In [58]:
# Set recordType to 'Religious'

religious_recordtype_id = df_sf_recordTypes.loc[
    (df_sf_recordTypes['DeveloperName'] == 'Religious') & (df_sf_recordTypes['SobjectType'] == 'Account'),
    'Id'
    ].iloc[0]  # Use .iloc[0] to get the first item if you're expecting exactly one match

print(religious_recordtype_id)

acc_religious_parents['RecordTypeId'] = religious_recordtype_id

acc_religious_parents.sample(10)

012Dx0000009TK0IAM


Description  \
252                      Society of the Divine Saviour   
219  Congregation of Our Lady of Charity of the Goo...   
232            Maronite Monks Of Jesus Mary and Joseph   
218      Sisters of Charity of the Blessed Virgin Mary   
247                             Brothers of Saint John   
189                              Ordo Sancti Benedicti   
238                           Heralds of the Good News   
215                   Misioneros del Rosario de Fátima   
186                                      Societas Iesu   
251                         Society of the Divine Word   

                                              Name  \
252                  Society of the Divine Saviour   
219                          Good Shepherd Sisters   
232                Sacred Heart Maronite Monastery   
218  Sisters of Charity of the Blessed Virgin Mary   
247                         Brothers of Saint John   
189         Benedictine Monks of Mount Angel Abbey   
238                       Heralds of the Good News   
215     Missionary Sisters of the Rosary of Fatima   
186                    Colombiere Jesuit Community   
251                     Society of the Divine Word   

                             mbfc__Abbreviation__c mbfc__Religious_Suffix__c  \
252                  Society of the Divine Saviour                       SDS   
219                          Good Shepherd Sisters                       RGS   
232                                 Maronite Monks                     MMJMJ   
218  Sisters of Charity of the Blessed Virgin Mary                       BVM   
247                         Brothers of Saint John                       CSJ   
189                                   Benedictines                       OSB   
238                       Heralds of the Good News                       HGN   
215           Missionaries of the Rosary of Fatima                      HMRF   
186                                        Jesuits                        SJ   
251                     Society of the Divine Word                       SVD   

    mbfc__Type_Members__c                  Archdpdx_Migration_Id__c  \
252                   Men                 societyofthedivinesaviour   
219                 Women  congregationofourladyofcharityofthegoods   
232                   Men         maronitemonksofjesusmaryandjoseph   
218                 Women    sistersofcharityoftheblessedvirginmary   
247                   Men                       brothersofsaintjohn   
189                   Men                       ordosanctibenedicti   
238                   Men                      heraldsofthegoodnews   
215                 Women              misionerosdelrosariodefátima   
186                   Men                              societasiesu   
251                   Men                    societyofthedivineword   

    Pontifical_or_Diocesan_Order__c Religious_Secular_Order__c  \
252                                                              
219                                            Religious Order   
232                                                              
218                Pontifical Order            Religious Order   
247                                                              
189                                            Religious Order   
238                                                              
215                  Diocesan Order                              
186                                            Religious Order   
251                                                              

    Religious_Type__c        RecordTypeId  
252      Congregation  012Dx0000009TK0IAM  
219      Congregation  012Dx0000009TK0IAM  
232      Congregation  012Dx0000009TK0IAM  
218      Congregation  012Dx0000009TK0IAM  
247      Congregation  012Dx0000009TK0IAM  
189      Congregation  012Dx0000009TK0IAM  
238      Congregation  012Dx0000009TK0IAM  
215      Congregation  012Dx0000009TK0IAM  
186      Congregation  

In [59]:
# Send to CSV
acc_religious_parents.to_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/staging/religious_order_staging.csv', encoding='utf-8-sig')

In [60]:
# Upsert to Salesforce
bulk_data = []
for row in acc_religious_parents.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

if run_upserts == 'True':
    religious_order_upsert = sf.bulk.Account.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
    df_rel_order_upsert = pd.DataFrame(religious_order_upsert)

df_rel_order_upsert

success  created                  id errors
0      True    False  001Dx00001FZmZjIAL     []
1      True    False  001Dx00001FZmZkIAL     []
2      True    False  001Dx00001FZmZlIAL     []
3      True    False  001Dx00001FZmb9IAD     []
4      True    False  001Dx00001FZmZmIAL     []
..      ...      ...                 ...    ...
57     True    False  001Dx00001FZmabIAD     []
58     True    False  001Dx00001FZmacIAD     []
59     True    False  001Dx00001FZmadIAD     []
60     True    False  001Dx00001FZmaeIAD     []
61     True    False  001Dx00001FZmbCIAT     []

[62 rows x 4 columns]

In [61]:
# Generate an Errors log
import csv

keys = religious_order_upsert[0].keys()

with open('results_files/religious_order_results', 'w', newline='') as csv_file:
    writer = csv.DictWriter(csv_file, keys)
    writer.writeheader()
    writer.writerows(religious_order_upsert)

In [62]:
# @title get SF Accounts
get_all_rel_accounts = f"Select id, Name, RecordTypeId, Type, Archdpdx_Migration_Id__c from Account where RecordTypeID = '{religious_recordtype_id}'"

print(religious_recordtype_id)

# get list of records, add to dataframe
sf_accounts = sf.query(get_all_rel_accounts)
df_sf_accounts = pd.DataFrame(sf_accounts['records'])
df_sf_accounts = df_sf_accounts.drop(columns = 'attributes')

df_sf_accounts.sample(10)

012Dx0000009TK0IAM


Id                                          Name  \
65   001Dx00001FZmaLIAT               Society of the Holy Child Jesus   
66   001Dx00001FZmaMIAT               Sacred Heart Maronite Monastery   
71   001Dx00001FZmaRIAT         Missionary Oblates of Mary Immaculate   
36   001Dx00001FZmZtIAL   Society of Domus Dei Holy House Monasteries   
48   001Dx00001FZma5IAD              Maryknoll Sisters of St. Dominic   
114  001Dx00001FaTj8IAF           Paulist Fathers, New York, NY (CSP)   
32   001Dx00001FZmZoIAL                      Apostolic Life Community   
9    001Dx00001FaTjHIAV  Society of the Divine Word, Techny, IL (SVD)   
37   001Dx00001FZmZuIAL                             Franciscan Friars   
110  001Dx00001FaTj4IAF      Heralds of the Good News, Portland (HGN)   

           RecordTypeId  Type                  Archdpdx_Migration_Id__c  
65   012Dx0000009TK0IAM  None                societyoftheholychildjesus  
66   012Dx0000009TK0IAM  None         maronitemonksofjesusmaryandjoseph  
71   012Dx0000009TK0IAM  None         missionaryoblatesofmaryimmaculate  
36   012Dx0000009TK0IAM  None    domusdeiclericalsocietyofapostoliclife  
48   012Dx0000009TK0IAM  None              maryknollsistersofst.dominic  
114  012Dx0000009TK0IAM  None                         RelCommunities_68  
32   012Dx0000009TK0IAM  None  apostoliclifecommunityofpriestsintheopus  
9    012Dx0000009TK0IAM  None                         RelCommunities_77  
37   012Dx0000009TK0IAM  None  ordofratrumminorumprovinceofsaintbarbara  
110  012Dx0000009TK0IAM  None                         RelCommunities_64

In [63]:
religious_order_mapping = df_sf_accounts.set_index('Archdpdx_Migration_Id__c')['Id'].to_dict()
# religious_order_mapping

### D) Religious Communities


In [64]:
acc_religious_staging = (acc_religious
                         .rename(columns={'Archdpdx_Migration_Id__c' : 'Parent_Archdpdx_Migration_Id__c'})
)

acc_religious_staging['ParentId'] = acc_religious_staging['Parent_Archdpdx_Migration_Id__c'].map(religious_order_mapping)

In [65]:
# Enrich the data

acc_religious_staging['Religious_Type__c'] = 'Local Community'
acc_religious_staging['Archdpdx_Migration_Id__c'] = 'RelCommunities_' + acc_religious_staging['Record Number'].astype('str')
acc_religious_staging['RecordTypeId'] = religious_recordtype_id
acc_religious_staging.drop(columns='Name', inplace=True)
acc_religious_staging.rename(columns={
    'Name, City': 'Name'
}, inplace=True)

acc_religious_staging.sample(5)

Record Number AccountRecordType  \
198             17         Religious   
225             49         Religious   
213             37         Religious   
250             76         Religious   
197             16         Religious   

                                                  Name Parish Name  \
198      Carmelite House of Studies, Mount Angel (OCD)         NaN   
225               Sisters of Reparation, Portland (SR)         NaN   
213                 Thu Thiem Sisters, Beaverton (LHC)         NaN   
250  Sons of Mary, Mother of Mercy, Umuahia, Nigeri...         NaN   
197      Brotherhood of the People of Praise, Portland         NaN   

     Archdiocese_Assigns_Clergy__c Locator_Description__c  BillingCity  \
198                          False                    NaN  Mount Angel   
225                          False                    NaN     Portland   
213                          False                    NaN    Beaverton   
250                          False                    NaN          NaN   
197                          False                    NaN     Portland   

    BillingState  Mailing Address Province BillingPostalCode  ...  \
198           OR                       NaN             97362  ...   
225           OR                       NaN             97214  ...   
213           OR                       NaN             97007  ...   
250          NaN                       NaN               NaN  ...   
197           OR                       NaN             97217  ...   

         BillingStreet Religious_Secular_Order__c  \
198  300 Humpert Ln NE            Religious Order   
225   2120 SE 24th Ave            Religious Order   
213  7361 SW 175th Ter                       None   
250                                          None   
197  7709 N Denver Ave                       None   

    Pontifical_or_Diocesan_Order__c            ParentId mbfc__Church_Type__c  \
198                            None  001Dx00001FZmZrIAL                  NaN   
225                  Diocesan Order  001Dx00001FZmaFIAT                  NaN   
213                            None  001Dx00001FZma4IAD                  NaN   
250                            None  001Dx00001FZmacIAD                  NaN   
197                  Diocesan Order  001Dx00001FZmZqIAL                  NaN   

              Parent_Archdpdx_Migration_Id__c        RecordTypeId Job_Id__c  \
198            ordocarmelitarumdiscalceatorum  012Dx0000009TK0IAM        81   
225  sistersofreparationofthesacredwoundsofje  012Dx0000009TK0IAM        81   
213          loversofthuthiemholycrosssisters  012Dx0000009TK0IAM        81   
250                  sonsofmary,motherofmercy  012Dx0000009TK0IAM        81   
197            brotherhoodofthepeopleofpraise  012Dx0000009TK0IAM        81   

    Religious_Type__c Archdpdx_Migration_Id__c  
198   Local Community        RelCommunities_17  
225   Local Community        RelCommunities_49  
213   Local Community        RelCommunities_37  
250   Local Community        RelCommunities_76  
197   Local Community        RelCommunities_16  

[5 rows x 74 columns]

In [66]:
acc_religious_staging_2 = acc_religious_staging[[
    'Name',
    'RecordTypeId',
    'Religious_Type__c',
    'BillingStreet',
    'BillingCity',
    'BillingState',
    'BillingPostalCode',
    'BillingCountry',
    'Phone',
    'Fax',
    'mbfc__Email__c',
    'Website',
    'mbfc__Abbreviation__c',
    'mbfc__Religious_Suffix__c',
    'mbfc__Type_Members__c',
    'Description',
    'Job_Id__c',
    'ParentId',
    'Archdpdx_Migration_Id__c'
    ]]

acc_religious_staging_2.sample(5)

Name        RecordTypeId  \
208      Carmelite Sisters, Discalced, Eugene (OCD)  012Dx0000009TK0IAM   
187  Abbey of Our Lady of Guadalupe, Carlton (OCSO)  012Dx0000009TK0IAM   
230                Society of Mary, Corvallis (SdM)  012Dx0000009TK0IAM   
251    Society of the Divine Word, Techny, IL (SVD)  012Dx0000009TK0IAM   
228   Sisters of St. Joseph of Peace, Eugene (CSJP)  012Dx0000009TK0IAM   

    Religious_Type__c                                      BillingStreet  \
208   Local Community  Carmel of Maria Regina, Monastery and Novitiat...   
187   Local Community   Abbey of Our Lady of Guadalupe\n9200 NE Abbey Rd   
230   Local Community                                      540 NW 9th St   
251   Local Community       Society of the Divine Word, Chicago Province   
228   Local Community             CSJP Western Region Office\nPO Box 248   

    BillingCity BillingState BillingPostalCode BillingCountry         Phone  \
208      Eugene           OR             97402            NaN  541-345-8649   
187     Carlton           OR             97111            NaN  503-852-7174   
230   Corvallis           OR             97330            NaN  541-754-1505   
251         NaN          NaN               NaN            NaN           NaN   
228    Bellevue           WA             98009            NaN  425-467-5400   

              Fax               mbfc__Email__c  \
208  541-345-4857       carmeleugene@gmail.com   
187  503-852-7748  community@trappistabbey.org   
230           NaN   sister.teresa@socmaria.org   
251           NaN                          NaN   
228  425-462-9760                          NaN   

                             Website       mbfc__Abbreviation__c  \
208  https://carmelitesinoregon.org/    Discalced Carmelite Nuns   
187    http://www.trappistabbey.org/                   Trappists   
230    https://www.socmaria.org/home             Society of Mary   
251      https://www.divineword.org/  Society of the Divine Word   
228                https://csjp.org/       Sisters of St. Joseph   

    mbfc__Religious_Suffix__c mbfc__Type_Members__c  \
208                       OCD                 Women   
187                      OCSO                   Men   
230                       SdM                 Women   
251                       SVD                   Men   
228                      CSJP                 Women   

                                           Description  Job_Id__c  \
208  The Carmel of Maria Regina is a cloistered com...         81   
187  The cloistered monastic cistercian community s...         81   
230  An Institute of consecrated missionary sisters...         81   
251                                                NaN         81   
228  Serving Sacred Heart RiverBend Medical Center,...         81   

               ParentId Archdpdx_Migration_Id__c  
208  001Dx00001FZmZrIAL        RelCommunities_32  
187  001Dx00001FZmZkIAL         RelCommunities_2  
230  001Dx00001FZmaKIAT        RelCommunities_54  
251  001Dx00001FZmadIAD        RelCommunities_77  
228  001Dx00001FZmaIIAT        RelCommunities_52

In [67]:
# Final Cleanup

acc_religious_staging_2 = acc_religious_staging_2.fillna('')

In [68]:
# @title Send to CSV
acc_religious_staging_2.to_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/staging/religious_community_staging.csv', encoding='utf-8-sig')

In [69]:
# @title Upsert to Salesforce
bulk_data = []
for row in acc_religious_staging_2.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

if run_upserts == 'True':
    religious_community_upsert = sf.bulk.Account.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
    df_rel_community_upsert = pd.DataFrame(religious_community_upsert)

df_rel_community_upsert

success  created                  id errors
0      True    False  001Dx00001FaTiFIAV     []
1      True    False  001Dx00001FaTiGIAV     []
2      True    False  001Dx00001FaTiHIAV     []
3      True    False  001Dx00001FaTiIIAV     []
4      True    False  001Dx00001FaTiJIAV     []
..      ...      ...                 ...    ...
65     True    False  001Dx00001FaTjHIAV     []
66     True    False  001Dx00001FaTjIIAV     []
67     True    False  001Dx00001FaTjJIAV     []
68     True    False  001Dx00001FaTjKIAV     []
69     True    False  001Dx00001FaTjLIAV     []

[70 rows x 4 columns]

### E) Religious Superiors


In [70]:
acc_rel_superiors = acc_religious_2[[
    'Name',
    'Major Superior Name',
    'Major Superior Phone',
    'Major Superior Email',
    'Archdpdx_Migration_Id__c']]


acc_rel_superiors['AccountId'] = acc_rel_superiors.Archdpdx_Migration_Id__c.map(religious_order_mapping)

# acc_rel_superiors.sample(5)

/var/folders/_g/p51k4k2d5fg45slnqjhgd3sc0000gn/T/ipykernel_24056/2858631496.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acc_rel_superiors['AccountId'] = acc_rel_superiors.Archdpdx_Migration_Id__c.map(religious_order_mapping)


In [71]:
# @title Parse Complex Names
def parse_names(df, column_name):
    # Convert all non-string entries to strings (handling NaN and other data types)
    df[column_name] = df[column_name].fillna('').apply(str)

    # Create a new DataFrame to store the name parts
    name_parts = pd.DataFrame()

    # Parse each name in the column
    name_parts['First Name'] = df[column_name].apply(lambda x: HumanName(x).first if x.strip() != '' else '')
    name_parts['Last Name'] = df[column_name].apply(lambda x: HumanName(x).last if x.strip() != '' else '')
    name_parts['Middle Name'] = df[column_name].apply(lambda x: HumanName(x).middle if x.strip() != '' else '')
    name_parts['Title'] = df[column_name].apply(lambda x: HumanName(x).title if x.strip() != '' else '')
    name_parts['Suffix'] = df[column_name].apply(lambda x: HumanName(x).suffix if x.strip() != '' else '')
    name_parts['Nickname'] = df[column_name].apply(lambda x: HumanName(x).nickname if x.strip() != '' else '')

    # Combine the original DataFrame with the name parts DataFrame
    result_df = pd.concat([df, name_parts], axis=1)
    return result_df



In [72]:
!pip install nameparser
from nameparser import HumanName
from nameparser.config import CONSTANTS

# Add dataset-specific Titles and Suffix constants for parsing
CONSTANTS.titles.add('Very', 'Rev.', 'Very Rev.', 'Sr.')
CONSTANTS.suffix_acronyms.add('FRS', 'OMI', 'OSA', 'OCD', 'OP', 'OC', 'FSE', 'OMV', 'SDB', 'SM', 'SFX', 'SP', 'OP', 'O.S.M', 'SNJM', 'OSF', 'HMRF', 'DD', 'CSJP', 'SDD', 'BVM', 'BVM - President' )


SetManager({'pmp', 'lmsw', 'ot', 'qsp', 'rci', 'ncso', 'chpa', 'rrt-accs', 'chrm', 'phd', 'dtr', 'shrm-scp', 'pta', 'rrt-sds', 'gphr', 'apn aprn', 'dvm', 'thd', 'cacts', 'lp', 'asa', 'mbs', 'mfa', 'cbt', 'cccm', 'ccca', 'cet', 'ipep', 'mpa', 'cpcm', 'aem', 'abr', 'fws', 'hccp', 'git', 'frs', 'capm', 'gcie', 'faspen', 'cbsp', 'csa', 'chba', 'lpss', 'ch', 'cxa', 'dss', 'llm', 'csi', 'iso', 'chpe', 'bds', 'gmr', 'acha', 'rn', 'md', 'ches', 'litl', 'kcvo', 'bvm - president', 'diplac', 'bt', 'fd', 'rpl', 'kcie', 'nrp', 'casp', 'ccna', 'fmva', 'cysa', 'faan', 'facog', 'erd', 'apr', 'rvm', 'caps', 'lvt', 'facem', 'cissp', 'aqp', 'crme', 'csre', 'fca', 'dcm', 'kcsi', 'ma', 'cfa', 'nbc-his', 'psm i', 'cfe', 'agsf', '8-vsb', 'om', 'mvo', 'bpi', 'mlse', 'pcc', 'chdm', 'sscp', 'bcss', 'cfcm', 'ciro', 'prm', 'ccp', 'cmfo', 'mlt', 'cusp', 'cplp', 'omi', 'enp', 'scmp', 'rrc', 'cwp', 'cdmp', 'cisa', 'lac', 'osf', 'ctfa', 'nicet iii', 'rpa', 'evp', 'faia', 'pfmp', 'fpc', 'khs/dhs', 'dfc', 'leed ap', 'p

In [73]:
# Parse Complex Names
acc_rel_superiors_parsed = parse_names(acc_rel_superiors, 'Major Superior Name')

/var/folders/_g/p51k4k2d5fg45slnqjhgd3sc0000gn/T/ipykernel_24056/520038690.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[column_name] = df[column_name].fillna('').apply(str)


In [74]:
# @title Final cleanup

acc_rel_superiors_staging = acc_rel_superiors_parsed.fillna('')

acc_rel_superiors_staging['Archdpdx_Migration_Id__c'] = acc_rel_superiors_staging['Major Superior Name'].apply(lambda x: x.replace(' ','').lower())

# Rename columns
acc_rel_superiors_staging = acc_rel_superiors_staging.rename(columns={
    'Major Superior Phone': 'Phone',
    'Major Superior Email': 'Email',
    'Title': 'Salutation',
    'First Name': 'FirstName',
    'Middle Name': 'MiddleName',
    'Last Name': 'LastName'
})

# Add job id
acc_rel_superiors_staging['Archdpdx_Job_Id__c'] = curr_job_id

# Drop columns
acc_rel_superiors_staging = acc_rel_superiors_staging.drop(columns=['Name', 'Major Superior Name', 'Nickname'])

# Drop empty rows
acc_rel_superiors_staging = acc_rel_superiors_staging[acc_rel_superiors_staging['LastName'].str.strip() != '']

acc_rel_superiors_staging.sample(10)

Phone                          Email  \
255          510-658-8722          provincial@opwest.org   
244                                                        
215  011 52 55 58 72 20 0    hmrf@misionerasdefatima.org   
228                                                        
201          510-536-3722                                  
246                                                        
254          510-658-8722          provincial@opwest.org   
199          510-658-8722          provincial@opwest.org   
230                        hermana.veronica@socmaria.org   
249       +39 06 61571401                pr@sancarlo.org   

                   Archdpdx_Migration_Id__c           AccountId    FirstName  \
255           veryrev.christopherfadok,o.p.  001Dx00001FZmZsIAL  Christopher   
244                   johnpaulouellette,cfr  001Dx00001FZmaWIAT         John   
215          candelarianavarroalvarado,hmrf  001Dx00001FZma6IAD   Candelaria   
228                 sisterandreanenzel,csjp  001Dx00001FZmaIIAT       Andrea   
201                    veryrev.davidgaa,ofm  001Dx00001FZmZuIAL          OFM   
246                ángelfernándezartime,sdb  001Dx00001FZmaYIAT        Ángel   
254  veryrev.christopherfadok,op,provincial  001Dx00001FZmZsIAL  Christopher   
199           veryrev.christopherfadok,o.p.  001Dx00001FZmZsIAL  Christopher   
230                     motherveronicalopez  001Dx00001FZmaKIAT     Veronica   
249                     fr.paolosottopietra  001Dx00001FZmabIAD        Paolo   

                LastName MiddleName Salutation          Suffix  \
255                Fadok             Very Rev.            O.P.   
244            Ouellette       Paul                        CFR   
215             Alvarado    Navarro                       HMRF   
228               Nenzel                Sister            CSJP   
201  Very Rev. David Gaa                                         
246               Artime  Fernández                        SDB   
254                Fadok             Very Rev.  OP, Provincial   
199                Fadok             Very Rev.            O.P.   
230                Lopez                Mother                   
249          Sottopietra                   Fr.                   

     Archdpdx_Job_Id__c  
255                  81  
244                  81  
215                  81  
228                  81  
201                  81  
246                  81  
254                  81  
199                  81  
230                  81  
249                  81

In [75]:
# @title Send to CSV
acc_rel_superiors_staging.to_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/staging/religious_superiors_staging.csv', encoding='utf-8-sig')

In [76]:
# @title Upsert to Salesforce

def find_existing_contact(sf, first_name, last_name):
    query = f"SELECT Id, Archdpdx_Migration_Id__c FROM Contact WHERE FirstName = '{first_name}' AND LastName = '{last_name}'"
    result = sf.query(query)
    return result['records']



bulk_data = []
for row in acc_rel_superiors_staging.itertuples(index=False):
    d = row._asdict()
    existing_contacts = find_existing_contact(sf, d['FirstName'], d['LastName'])
    if existing_contacts:
        # Update existing contact with external ID
        d['Id'] = existing_contacts[0]['Id']
        bulk_data.append(d)
    else:
        bulk_data.append(d)


if run_upserts == 'True':
    religious_superior_upsert = sf.bulk.Contact.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
    df_rel_superior_upsert = pd.DataFrame(religious_superior_upsert)

df_rel_superior_upsert

success  created                  id  \
0     False    False                None   
1      True    False  003Dx00000m0jAWIAY   
2      True    False  003Dx00000m0jAXIAY   
3      True    False  003Dx00000m0jAYIAY   
4     False     True                None   
5      True    False  003Dx00000m0jAZIAY   
6      True    False  003Dx00000m0jAaIAI   
7     False    False                None   
8      True    False  003Dx00000m0jAbIAI   
9      True    False  003Dx00000m0jAcIAI   
10     True    False  003Dx00000m0jAdIAI   
11     True    False  003Dx00000m0jAeIAI   
12     True    False  003Dx00000m0jAfIAI   
13     True    False  003Dx00000m0jAgIAI   
14     True    False  003Dx00000m0jAhIAI   
15     True    False  003Dx00000m0jAiIAI   
16     True    False  003Dx00000m0jAjIAI   
17     True    False  003Dx00000m0jAkIAI   
18     True    False  003Dx00000m0jAlIAI   
19     True    False  003Dx00000m0jAmIAI   
20     True    False  003Dx00000m0jAnIAI   
21     True    False  003Dx00000m0jAoIAI   
22     True    False  003Dx00000m0jApIAI   
23     True    False  003Dx00000m0jAqIAI   
24     True    False  003Dx00000m0jArIAI   
25     True    False  003Dx00000m0jAsIAI   
26     True    False  003Dx00000m0jAtIAI   
27    False     True                None   
28    False    False                None   
29    False     True                None   
30     True    False  003Dx00000m0jAuIAI   
31     True    False  003Dx00000m0jAvIAI   
32     True    False  003Dx00000m0jAwIAI   
33     True    False  003Dx00000m0jAxIAI   
34     True    False  003Dx00000m0jAyIAI   
35     True    False  003Dx00000m0jAzIAI   
36     True    False  003Dx00000m0jB0IAI   
37     True    False  003Dx00000m0jB1IAI   
38     True    False  003Dx00000m0jB2IAI   
39     True    False  003Dx00000m0jB3IAI   
40     True    False  003Dx00000m0jB4IAI   
41    False    False                None   

                                               errors  
0   [{'statusCode': 'DUPLICATE_VALUE', 'message': ...  
1                                                  []  
2                                                  []  
3                                                  []  
4   [{'statusCode': 'INVALID_EMAIL_ADDRESS', 'mess...  
5                                                  []  
6                                                  []  
7   [{'statusCode': 'DUPLICATE_VALUE', 'message': ...  
8                                                  []  
9                                                  []  
10                                                 []  
11                                                 []  
12                                                 []  
13                                                 []  
14                                                 []  
15                                                 []  
16                                                 []  
17                                                 []  
18                                                 []  
19                                                 []  
20                                                 []  
21                                                 []  
22                                                 []  
23                                                 []  
24                                                 []  
25                                                 []  
26                                                 []  
27  [{'statusCode': 'STRING_TOO_LONG', 'message': ...  
28  [{'statusCode': 'DUPLICATE_VALUE', 'message': ...  
29  [{'statusCode': 'INVALID_EMAIL_ADDRESS', 'mess...  
30                                                 []  
31                                                 []  
32                                                 []  
33                                                 []  
34                                                 []  
35                                                 []  
36                                     

In [77]:
# @title Update Religious Communities with Rel. Superior

# TBD: It would take much less time to simply do this post-migration manually.

# CONTACTS


## Extract


In [227]:
df_contacts = (pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/People.csv')
               .set_index('Record Number', verify_integrity=True)
               .drop(index='recNum') # Drops the extra row that replicates the labels
               .rename(columns=lambda x: x.replace(' ', '_')) # Remove whitespace in column names
)

df_contacts.sample(10)


Common_Name          Sort_Name    Type(s)  \
Record Number                                                              
65                         Mr. Mark Wonser   wonser mark mark    Archive   
2515           Sr. Mary Ellen Hanson, SSMO  hanson mary ellen  Religious   
1139                     Rev. Alan Kennedy       kennedy alan     Priest   
1748                     Ms. Cyndie Harris      harris cyndie      Staff   
3104                      Ms. Kate Welborn       welborn kate      Staff   
3323                     Mrs. Sara Edmonds       edmonds sara       Wife   
2245                     Ms. Whitney DePew      depew whitney      Staff   
1706                    Ms. Parri Van Dyke     van dyke parri      Staff   
2527               Sr. Judith Henigin, OSB     henigin judith  Religious   
1618                     Mr. Wells O’Byrne       obyrne wells      Staff   

              Clergy_Status Religious_Status  Login_ID  \
Record Number                                            
65                      NaN              NaN       NaN   
2515                    NaN         Deceased       NaN   
1139               Deceased              NaN       NaN   
1748                    NaN              NaN       NaN   
3104                    NaN              NaN  kwelborn   
3323                    NaN              NaN       NaN   
2245                    NaN              NaN       NaN   
1706                    NaN              NaN       NaN   
2527                    NaN         Deceased       NaN   
1618                    NaN              NaN       NaN   

                                                        Password  \
Record Number                                                      
65                                                           NaN   
2515                                                         NaN   
1139                                                         NaN   
1748                                                         NaN   
3104           cce54aa4d9712fa95c6a2b7492d55c24992c31b114f09b...   
3323                                                         NaN   
2245                                                         NaN   
1706                                                         NaN   
2527                                                         NaN   
1618                                                         NaN   

              Password_Must_be_Changed Access_Permission Spouse  ...  \
Record Number                                                    ...   
65                                 NaN               NaN      0  ...   
2515                               NaN               NaN      0  ...   
1139                               NaN               NaN      0  ...   
1748                               NaN               NaN      0  ...   
3104                               Yes            marcom      0  ...   
3323                               NaN               NaN   3322  ...   
2245                               NaN               NaN      0  ...   
1706                               NaN               NaN      0  ...   
2527                               NaN               NaN      0  ...   
1618                               NaN               NaN      0  ...   

                CARA_Ethnicity Seminarian_Status Other_Diaconal_Ministry  \
Record Number                                                              
65             Caucasian/white               NaN                     NaN   
2515                       NaN               NaN                     NaN   
1139                       NaN               NaN                     NaN   
1748                       NaN               NaN                     NaN   
3104                       NaN               NaN                     NaN   
3323                       NaN               NaN                     NaN   
2245                       NaN               NaN                     NaN   
1706                       NaN               NaN       

#### Get Photos


In [228]:
import os
import pandas as pd

# def list_jpeg_files(directory):
#     data = []
#     for filename in os.listdir(directory):
#         if filename.endswith(".jpeg") or filename.endswith(".jpg"):  # Checking for jpeg files
#             full_path = os.path.join(directory, filename)
#             data.append({'Filename': filename, 'Full Path': full_path})
#     return pd.DataFrame(data)

# # Specify your directory
# directory = '/content/drive/Shareddrives/Clients/ADPDX (Portland)/Data/Clergy DB/sql_backup/archdpdx.info backups/public_html/people/graphics/portraits/large'
# jpeg_files_df = list_jpeg_files(directory)


In [229]:
# # Query for the Library
# library_query = "SELECT Id, Name FROM ContentWorkspace WHERE Name = 'ADPDX Person Profile Photos'"
# library_result = sf.query(library_query)

# # Check if the library exists and get its ID
# if library_result['records']:
#     library_id = library_result['records'][0]['Id']
#     print(f"Library ID: {library_id}")

#     # Query for the Folder within the Library
#     folder_query = f"SELECT Id, Name FROM ContentFolder WHERE ParentContentFolderId = '{library_id}'"
#     folder_result = sf.query(folder_query)

#     # Check if the folder exists and get its ID
#     if folder_result['records']:
#         folder_id = folder_result['records'][0]['Id']
#         print(f"Folder ID: {folder_id}")
#     else:
#         print("Folder 'Large JPEGs' not found in the library.")
# else:
#     print("Library 'ADPDX Person Profile Photos' not found.")

## Analysis

Here we check the various columns and their types, count where values exist, count of unique values, sample data, etc.

DF shape:

- 142 columns
- 3017 rows


In [230]:
# Check the original shape of the imported CSV
print(f"Shape of original data set: {df_contacts.shape}")

# export to csv a list of the contact fields with count, unique, top, freq
contacts_describe = df_contacts.describe(include='all').transpose()
contacts_describe.to_csv(f'/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/analysis/contacts_describe.csv')

df_contacts.describe(include='all').transpose()  #initial analysis of the Contacts table

Shape of original data set: (3016, 141)


count unique                top  freq
Common_Name       3016   3011   Ms. Leslie Jones     2
Sort_Name         3016   3009     nguyen anthony     3
Type(s)           3016     29              Staff  1139
Clergy_Status     1138      8    Transferred Out   462
Religious_Status   902      4             Active   456
...                ...    ...                ...   ...
Place_of_Work      269    133  Mount Angel Abbey    37
Volunteer_Place     54     47       Mary’s Woods     4
Type_of_Work       276    117  Pastoral Ministry    30
Work_Load          262      2          Full Time   230
Work_Title         262    163           Reverend    26

[141 rows x 4 columns]

In [231]:
unique_languages = df_contacts['Languages'].unique()
unique_languages

array([nan, 'English,Spanish', 'Igbo', 'English, Spanish',
       'Spanish, Mayaqeqchi', 'Spanish (Mass only)',
       'Latin Mass and written translation. Read French, Italian, Spanish.',
       'Spanish', 'Hindi, Konkani, Tamil',
       'French (fluent), Spanish (beginner), Latin (beginner)',
       'German, Spanish, Italian, French', 'Kiswahili, Kichagga',
       'Spanish (English is second language)',
       'German, Spanish, Italian, Latin Mass',
       'English, Spanish, Italian', 'Spanish, Italian', 'English',
       'Bicolango, Tagalog, Spanish', 'Spanish, Italian, Latin Mass',
       'Italian', 'Tagalog, English, Spanish',
       'French, Italian, Aramaic (modern), Spanish', 'Vietnamese',
       'German, Spanish', 'English,Spanish,Italian',
       'Conversant in Italian and Spanish, some facility with Latin and German',
       'English, Spanish, Latin Mass', 'Italian, Spanish',
       'Konkani, Hindi, Marathi, Spanish',
       'Tagalog, Bicol, Spanish (Mass only)', 'Spanish, E

In [232]:
import re
import numpy as np


def deduplicate_languages(list_languages):
    # Define a regular expression pattern to match periods and punctuation
    punctuation_pattern = r'[.,!?;:"]'

    # Flatten the array and filter out NaN values
    flattened_languages = [re.sub(punctuation_pattern, '', lang) for sublist in list_languages if pd.notna(sublist) for lang in sublist.split(',')]

    # Deduplicate the list of languages
    unique_languages = list(set(flattened_languages))

    return unique_languages


# Example usage:
unique_languages = deduplicate_languages(unique_languages)
print(unique_languages)


['', 'Latin Mass', ' Spanish Mass', ' Hindi', ' Tamil', 'Tamil', 'English', ' Spanish (small bits)', 'Conversant in Italian and Spanish', 'French', ' Hebrew', 'Latin', ' Latin', 'Igbo', ' Marathi', ' Tagalog', ' Swahili Mass', 'Polish', 'Tamil (Indian)', ' Hebrew (reading)', 'Kannada', ' Konkawin', ' Little Spanish', ' English', 'Konkani', 'Spanish (English is second language)', ' Kichagga', ' Ukrainian', ' Bicol', 'Chuukese', ' Arabic', ' Greek', ' Latin Mass', 'German', 'Kisii', ' Swahili', ' Spanish (Mass only)', ' Chamorro', 'Vietnamese', ' Maya Q’eqchi’', ' Englsih', 'Afrikaans', ' Vietnamese (semi-fluent)', ' but can do rituals)', 'French (small bits)', 'Kiswahili', ' Mayaqeqchi', ' Spanish', ' Biblical Hebrew & Aramaic', 'Crijolle', ' Russian', 'Latin Mass and written translation Read French', ' Latin (beginner)', ' a little Spanish(not conversational', ' German', ' Aramaic (modern)', ' Vietnamese', ' Portuguese', 'Korean', ' Spanish (beginner)', ' Konkani', 'French (fluent)', '

## Transform


In [233]:
# init list of columns NOT to be loaded as Contact attributes
misc_columns_to_drop = [
    'Password',
    'Password_Must_be_Changed',
    'Common_Name',
    'Sort_Name',
    'Private_Address_Province'
]

affiliation_columns = [
    'Baptism_Date',
    'Place_of_Baptism',
    'Confirmation_Date',
    'Place_of_Confirmation',
    'Received_Date',
    'Parish_of_Record',
    'Marriage_Date',
    'Place_of_Marriage',
    'Date_of_First_Vows',
    'Date_of_Final_Vows',
    'Reader_Date',
    'Acolyte_Date',
    'Bachelor_Degree_Year',
    'Bachelor_Degree_Type',
    'Bachelor_Degree_Institution',
    'Graduate_1_Degree_Institution',
    'Graduate_1_Degree_Type',
    'Graduate_1_Degree_Year',
    'Graduate_2_Degree_Institution',
    'Graduate_2_Degree_Type',
    'Graduate_2_Degree_Year',
    'Graduate_3_Degree_Institution',
    'Graduate_3_Degree_Type',
    'Graduate_3_Degree_Year',
    'Graduate_4_Degree_Institution',
    'Graduate_4_Degree_Type',
    'Graduate_4_Degree_Year',
    'Diaconal_Ordination_Date',
    'Diaconal_Ordination_Place',
    'Diaconal_Ordination_Prelate',
    'Presbyteral_Ordination_Date',
    'Presbyteral_Ordination_Place',
    'Presbyteral_Ordination_Prelate',
    'Episcopal_Ordination_Date',
    'Episcopal_Ordination_Place',
    'Episcopal_Ordination_Prelate',
    'Incardinated_From_Date',
    'Incardinated_From_Diocese',
    'Excardinated_To_Diocese',
    'Excardinated_To_Date',
    'Faculties',
    'Faculties_Granted_Date',
    'Faculties_Restricted_Date',
    'Faculties_Withdrawn_Date',
]

In [234]:
# These fields need to be KEPT but while building the SF upsert flow these are dropped temporarily until mapping logic is included.
# TODO

fields_not_yet_mapped = [
    'Nickname',
    'Spouse',
    'Father_Full_Name',
    'Mother_Full_Maiden_Name',
    'Mailing_Address_2',
    'Mailing_Address_Province',
    'Preferred_Address',
    'Private_Address__Street__s',
    'Private_Address_2',
    'Private_Address__City__s',
    'Private_Address__StateCode__s',
    'Private_Address__PostalCode__s',
    'Private_Address__CountryCode__s',
    'Preferred_Email',
    'Preferred_Phone',
    'Social_Security_Account_Number__c',  # The data is encrypted
    'Languages',  # Picklist is restricted, in MFC package. Needs unrestricting before I can migrate data.
    
    # Can remove the below commented out lines once the migration is working smoothly
    # 'Seminarian_Student_Debt',
    # 'Seminarian_Medical_Benefits',
    # 'Candidacy_Date',
    # 'Accepted_to_Formation_Date',
    # 'Formation_Withdrawn_Date',
    # 'Formation_Deferred_Date',
    # 'Formation_Terminated_Date',
    # 'Terminate_or_Defer_Note',
    # 'CARA_Highest_Ed_Level',
    # 'Letter_of_Good_Standing_Date',
    # 'Religious_In_Archdiocese_Date',
    # 'Last_Retreat_Date',
    # 'Last_Educ_Requirement_Date',
    # 'Policy_Manual_Acknowledgement_Date',
    # 'Harassment_Prevention_Course_Date',
    # 'Standards_of_Conduct_Date',
    # 'Last_Background_Check_Date',
    # 'Last_Child_Protection_Training_Date',
    # 'Senior_Status_Date', 
    # 'Laicized_Date', 
    # 'Coverage_Availability', 
    # 'Advanced_Directive_Date',
    # 'End_of_Life_Plan_Date',
    # 'Will_Date',
    # 'Will_Note',
    # 'CIC_489_File',
    # 'CARA_Ethnicity',
    # 'Seminarian_Status',
    # 'Other_Diaconal_Ministry',
    # 'Spiritual_Director_Authorized',
    # 'Place_of_Work',
    # 'Volunteer_Place',
    # 'Type_of_Work',
    # 'Work_Load',
    # 'Work_Title',
    # 'Out_of_Diocese_Date',

    'Incardinated_Now',
    'Serving_Now',
    'Ordination_Diocese',
    'Registered_Parish',
    'Link_to_Religious_Community', # Requires a lookup to AccountID


]

In [235]:
# UDF to combine multiple Mailing Street Address lines into one

def combine_addresses(row, *columns):
    address_parts = []
    for col in columns:
        address_parts.append(row[col])
    return 'CHAR(10)'.join(address_parts)


In [236]:
df_contact_staging = (df_contacts
                      .drop(columns='Salutation')
                      .rename(columns={
                          'Clergy_Status' : 'ADPDX_Clergy_Status__c',
                          'Religious_Status' : 'ADPDX_Religious_Status__c',
                          'Login_ID' : 'ADPDX_Login_ID__c',
                          'Access_Permission': 'ADPDX_Access_Permission__c',
                          'Title': 'Salutation',
                          'Christian_Name': 'FirstName',
                          'Middle_Name(s)': 'MiddleName',
                          'Surname': 'LastName',
                          'Suffix': 'Suffix',
                          #Mailing_Address & Mailing_Address_2
                          'Mailing_Address' : 'MailingStreet',
                          'Mailing_Address_City': 'MailingCity',
                          'Mailing_Address_State': 'MailingState',
                          #'Mailing_Address_Province': 'MailingProvince'
                          'Mailing_Address_Postal_Code': 'MailingPostalCode',
                          'Mailing_Address_Country': 'MailingCountry',
                          'Private_Address': 'Private_Address__Street__s',
                          'Private Address 2': 'Private_Address__Street__s',
                          'Private_Address_City': 'Private_Address__City__s',
                          'Private_Address_State': 'Private_Address__StateCode__s',
                          'Private_Address_Postal_Code': 'Private_Address__PostalCode__s',
                          'Private_Address_Country': 'Private_Address__CountryCode__s',
                          # 'Preferred_Address'
                          'Work_Phone': 'npe01__WorkPhone__c',
                          'Home_Phone': 'HomePhone',
                          'Cell_Phone': 'MobilePhone',
                        #   'Preferred_Phone': 'npe01__PreferredPhone__c',
                          # IF Preferred phone contains, 'do not publish'
                          'Work_Email' : 'npe01__WorkEmail__c',
                          'Archdiocesan_Email': 'npe01__AlternateEmail__c',
                          'Home_Email': 'npe01__HomeEmail__c',
                        #   'Preferred_Email': 'npe01__Preferred_Email__c',
                          # IF Preferred email contains 'do not publish''
                          'Directory_Include': 'Directory_Include__c',
                          'Directory_Include_Middle_Name': 'Directory_Include_Middle_Name__c',
                          'Directory_Include_Suffix': 'Directory_Include_Suffix__c',
                          'Suppress_From_Reports': 'Suppress_From_Reports__c',
                          'Send_Group_Mail_and_Email': 'Send_Group_Mail_and_Email__c',
                          'Birth_Date': 'Birthdate',
                          'Place_of_Birth': 'mbfc__Place_of_Birth__c',
                          'Foreign_Born': 'Foreign_Born__c',
                          'Foreign_Citizenship': 'Foreign_Citizenship__c',
                          'Immigration_Status': 'Immigration_Status__c',
                          'Passport/Visa_Expiration_Date': 'Passport_Visa_Expiration_Date__c',
                          'Social_Security_Account_Number': 'Social_Security_Account_Number__c',
                          'Deceased_Date': 'mbfc__Date_of_Death__c',
                        #   'Languages': 'Languages__c',
                          'Out_of_Diocese_Date': 'mbfc__Date_Left_Diocese__c', 
                          'CARA_Ethnicity': 'adpdx_CARA_Ethnicity__c',
                          'Seminarian_Status': 'adpdx_Seminarian_Status__c',
                          'Other_Diaconal_Ministry': 'adpdx_Other_Diaconal_Ministry__c',
                          'Spiritual_Director_Authorized': 'adpdx_Spiritual_Director_Authorized__c',
                          'Place_of_Work': 'adpdx_Place_of_Work__c',
                          'Volunteer_Place': 'adpdx_Volunteer_Place__c',
                          'Type_of_Work': 'adpdx_Type_of_Work__c',
                          'Work_Load': 'adpdx_Work_Load__c',
                          'Work_Title': 'adpdx_Work_Title__c',
                          'Coverage_Availability': 'adpdx_Coverage_Availability__c', 
                          'Advanced_Directive_Date': 'adpdx_Advanced_Directive_Date__c',
                          'End_of_Life_Plan_Date': 'adpdx_End_of_Life_Plan_Date__c',
                          'Will_Date': 'adpdx_Will_Date__c',
                          'Will_Note': 'adpdx_Will_Note__c',
                          'CIC_489_File': 'adpdx_CIC_489_File__c',
                          'Senior_Status_Date': 'adpdx_Senior_Status_Date__c', 
                          'Laicized_Date': 'adpdx_Laicized_Date__c',
                          'Seminarian_Student_Debt': 'adpdx_Seminarian_Student_Debt__c',
                          'Seminarian_Medical_Benefits': 'adpdx_Seminarian_Medical_Benefits__c',
                          'Candidacy_Date': 'adpdx_Candidacy_Date__c',
                          'Accepted_to_Formation_Date': 'adpdx_Accepted_to_Formation_Date__c',
                          'Formation_Withdrawn_Date': 'adpdx_Formation_Withdrawn_Date__c',
                          'Formation_Deferred_Date': 'adpdx_Formation_Deferred_Date__c',
                          'Formation_Terminated_Date': 'adpdx_Formation_Terminated_Date__c',
                          'Terminate_or_Defer_Note': 'adpdx_Terminate_or_Defer_Note__c',
                          'CARA_Highest_Ed_Level': 'adpdx_CARA_Highest_Ed_Level__c',
                          'Letter_of_Good_Standing_Date': 'adpdx_Letter_of_Good_Standing__c',
                          'Religious_In_Archdiocese_Date': 'mbfc__Date_of_Arrival_in_Diocese__c',
                          'Last_Retreat_Date': 'adpdx_Last_Retreat_Date__c',
                          'Last_Educ_Requirement_Date': 'adpdx_Last_Educ_Requirement_Date__c',
                          'Policy_Manual_Acknowledgement_Date': 'adpdx_Policy_Manual_Acknowledgement_Date__c',
                          'Harassment_Prevention_Course_Date': 'adpdx_Harassment_Prevention_Course_Date__c',
                          'Standards_of_Conduct_Date': 'adpdx_Standards_of_Conduct_Date__c',
                          'Last_Background_Check_Date': 'adpdx_Last_Background_Check_Date__c',
                          'Last_Child_Protection_Training_Date': 'adpdx_Last_Child_Protection_Training__c',

                          })
                      .assign(Bi_Ritual__c=lambda x: x['Type(s)'].str.contains('Biritual'))
                      .assign(Non_Latin_Rite__c=lambda x: x['Type(s)'].str.contains('Non-Latin Rite'))
                      .assign(Archdpdx_Migration_Id__c=lambda x: x.index)
                    #   .assign(Mailing_Address=lambda row: combine_addresses(row, 'Mailing_Address', 'Mailing_Address_2'), axis=1) #FIXME
                      .drop(columns=misc_columns_to_drop)
                      .drop(columns=affiliation_columns)
                      .drop(columns=fields_not_yet_mapped)

        )


### Private Address Handling


In [237]:
# df_contact_staging.loc[:,'Private_Address__Street__s':'Private_Address__CountryCode__s'][~df_contact_staging['Private_Address__StateCode__s'].isna()]

In [238]:
# df_contact_staging['Private_Address__CountryCode__s'] = df_contact_staging.apply(lambda row: 'United States' if pd.notnull(row['Private_Address__StateCode__s']) and pd.isnull(row['Private_Address__CountryCode__s']) else row['Private_Address__CountryCode__s'], axis=1)

### Handle Boolean Fields


In [239]:
boolean_columns_to_convert = ['Foreign_Born__c', 'Directory_Include__c', 'Directory_Include_Middle_Name__c', 'Directory_Include_Suffix__c',
       'Suppress_From_Reports__c', 'Send_Group_Mail_and_Email__c', ]

df_contact_staging[boolean_columns_to_convert] = df_contact_staging[boolean_columns_to_convert].replace({'Yes': True, 'No': False})


In [240]:
df_contact_staging[boolean_columns_to_convert] = df_contact_staging[boolean_columns_to_convert].fillna(False)

df_contact_staging[boolean_columns_to_convert].sample(5)

Foreign_Born__c  Directory_Include__c  \
Record Number                                          
3024                     False                 False   
2646                     False                  True   
3188                     False                 False   
2616                     False                 False   
1200                     False                 False   

               Directory_Include_Middle_Name__c  Directory_Include_Suffix__c  \
Record Number                                                                  
3024                                      False                        False   
2646                                      False                        False   
3188                                      False                        False   
2616                                      False                        False   
1200                                      False                        False   

               Suppress_From_Reports__c  Send_Group_Mail_and_Email__c  
Record Number                                                          
3024                              False                          True  
2646                              False                          True  
3188                              False                          True  
2616                              False                          True  
1200                              False                          True

### Set Contact Record Type


In [241]:
# Set Record Type

# Go down row by row and check the 'Type(s)' columns, check for certain words that are keys in a dictionary, and
# the that row's 'Type(s)' field contains a string that is in the a key in a dictionary the update another columns
# called 'ContactRecordType' with the paired value.

contact_type_map = {
    'Bishop': 'Priest',
    'Diaconate': 'Lay_Person',
    'Permanent Deacon': 'Permanent_Deacon',
    'Priest': 'Priest',
    'Staff': 'Lay_Person',
    'Seminarian': 'Lay_Person',
    'Wife': 'Lay_Person',
    'Religious': 'Religious',
    'Seminary Applicant': 'Lay_Person',
    'Transitional Deacon': 'Priest',
    'Archive': 'Lay_Person'
}

def update_contact_record_type(row):
    for key, value in contact_type_map.items():
        if key in row['Type(s)']:
            return value
    return None

df_contact_staging['ContactRecordType'] = df_contact_staging.apply(update_contact_record_type, axis=1)

In [242]:
# Map in the RecordTypeIDs
df_contact_staging['RecordTypeID'] = df_contact_staging['ContactRecordType'].map(record_types_mapping)

In [243]:
# Check for any Contacts who are missing a RecordTypeId
df_contact_staging[df_contact_staging['RecordTypeID'].isna()]

Empty DataFrame
Columns: [Type(s), ADPDX_Clergy_Status__c, ADPDX_Religious_Status__c, ADPDX_Login_ID__c, ADPDX_Access_Permission__c, Salutation, FirstName, MiddleName, LastName, Suffix, MailingStreet, MailingCity, MailingState, MailingPostalCode, MailingCountry, npe01__WorkPhone__c, HomePhone, MobilePhone, npe01__WorkEmail__c, npe01__AlternateEmail__c, npe01__HomeEmail__c, Directory_Include__c, Directory_Include_Middle_Name__c, Directory_Include_Suffix__c, Suppress_From_Reports__c, adpdx_Seminarian_Student_Debt__c, adpdx_Seminarian_Medical_Benefits__c, Send_Group_Mail_and_Email__c, Birthdate, mbfc__Place_of_Birth__c, Foreign_Born__c, Foreign_Citizenship__c, Immigration_Status__c, Passport_Visa_Expiration_Date__c, adpdx_Accepted_to_Formation_Date__c, adpdx_Candidacy_Date__c, adpdx_Formation_Withdrawn_Date__c, adpdx_Formation_Deferred_Date__c, adpdx_Formation_Terminated_Date__c, adpdx_Terminate_or_Defer_Note__c, adpdx_CARA_Highest_Ed_Level__c, adpdx_Letter_of_Good_Standing__c, mbfc__Date_of_Arrival_in_Diocese__c, adpdx_Last_Retreat_Date__c, adpdx_Last_Educ_Requirement_Date__c, adpdx_Policy_Manual_Acknowledgement_Date__c, adpdx_Harassment_Prevention_Course_Date__c, adpdx_Standards_of_Conduct_Date__c, adpdx_Last_Background_Check_Date__c, adpdx_Last_Child_Protection_Training__c, mbfc__Date_Left_Diocese__c, adpdx_Senior_Status_Date__c, adpdx_Laicized_Date__c, mbfc__Date_of_Death__c, adpdx_Coverage_Availability__c, adpdx_Advanced_Directive_Date__c, adpdx_End_of_Life_Plan_Date__c, adpdx_Will_Date__c, adpdx_Will_Note__c, adpdx_CIC_489_File__c, adpdx_CARA_Ethnicity__c, adpdx_Seminarian_Status__c, adpdx_Other_Diaconal_Ministry__c, adpdx_Spiritual_Director_Authorized__c, adpdx_Place_of_Work__c, adpdx_Volunteer_Place__c, adpdx_Type_of_Work__c, adpdx_Work_Load__c, adpdx_Work_Title__c, Bi_Ritual__c, Non_Latin_Rite__c, Archdpdx_Migration_Id__c, ContactRecordType, RecordTypeID]
Index: []

[0 rows x 74 columns]

### Email Validation


In [244]:
# !pip install email_validator
from email_validator import validate_email, EmailNotValidError

# function that validates an email and if it is invalid it returns nothing
def validate_email_address(email):
    if isinstance(email, float):
        return None
    try:
        v = validate_email(email)
        return v.email
    except EmailNotValidError:
        return None


In [245]:
# init a list of Email columns
# email_columns = ['npe01__HomeEmail__c', 'npe01__WorkEmail__c', 'npe01__AlternateEmail__c']

# df_contact_staging[email_columns] = df_contact_staging[email_columns].applymap(validate_email_address)

### Final Dataframe Cleanup


In [246]:
# drop columns that are no longer needed
del df_contact_staging['Type(s)']
del df_contact_staging['ContactRecordType']

In [262]:
# convert '' to NaN
df_contact_staging.replace("", np.nan, inplace=True)

# convert NaN to None
df_contact_staging = df_contact_staging.where(df_contact_staging.notnull(), None)


In [267]:
df_contact_staging

ADPDX_Clergy_Status__c ADPDX_Religious_Status__c  \
Record Number                                                    
2766                 Transferred Out                      None   
2337                            None                      None   
3244                            None                      None   
3295                            None                      None   
2164                            None                      None   
...                              ...                       ...   
1670                            None                      None   
2755                            None                    Active   
1962                            None                      None   
2202                            None                      None   
1866                            None                      None   

              ADPDX_Login_ID__c ADPDX_Access_Permission__c Salutation  \
Record Number                                                           
2766                   sabukaka                       None       Rev.   
2337                       None                       None        Mr.   
3244                       None                       None        Mr.   
3295                       None                       None        Ms.   
2164                       None                       None        Ms.   
...                         ...                        ...        ...   
1670                       None                       None        Ms.   
2755                  dzorrilla                       None        Br.   
1962                       None                       None        Ms.   
2202                       None                       None        Ms.   
1866                       None                       None        Ms.   

              FirstName MiddleName  LastName Suffix  \
Record Number                                         
2766            Stephen    Ozovehe  Abaukaka   None   
2337            Rogelio       None   Acevedo   None   
3244               Sean       None   Ackroyd   None   
3295            Sherril       None     Acton   None   
2164            Barbara       None     Adams   None   
...                 ...        ...       ...    ...   
1670              Jenny       None  Zomerdyk   None   
2755             Daniel       None  Zorrilla   None   
1962                Kim       None     Zuber   None   
2202              Agnes       None    Zueger   None   
1866             Laurie       None    Zupsic   None   

                                MailingStreet  ... adpdx_Place_of_Work__c  \
Record Number                                  ...                          
2766                  Brighton Hospice Office  ...                   None   
2337                        St. Pius X Parish  ...                   None   
3244                          St. Mary Parish  ...                   None   
3295              Marist Catholic High School  ...                   None   
2164                         St. Henry Parish  ...                   None   
...                                       ...  ...                    ...   
1670            Shepherd of the Valley Parish  ...                   None   
2755           Félix Rougier House of Studies  ...                   None   
1962                      St. Boniface Parish  ...                   None   
2202              Our Lady of the Lake Parish  ...                   None   
1866                         St. Clare Parish  ...                   None   

              adpdx_Volunteer_Place__c adpdx_Type_of_Work__c  \
Record Number                                                  
2766                              None                  None   
2337                              None                  None   
3244                              None                  None   
3295                              None                  None   
2164                              None                  None   
...                                ... 

In [261]:
# df_contact_staging_2 = df_contact_staging.where(df_contact_staging.notnull(), None)

In [263]:
df_contact_staging.columns


Index(['ADPDX_Clergy_Status__c', 'ADPDX_Religious_Status__c',
       'ADPDX_Login_ID__c', 'ADPDX_Access_Permission__c', 'Salutation',
       'FirstName', 'MiddleName', 'LastName', 'Suffix', 'MailingStreet',
       'MailingCity', 'MailingState', 'MailingPostalCode', 'MailingCountry',
       'npe01__WorkPhone__c', 'HomePhone', 'MobilePhone',
       'npe01__WorkEmail__c', 'npe01__AlternateEmail__c',
       'npe01__HomeEmail__c', 'Directory_Include__c',
       'Directory_Include_Middle_Name__c', 'Directory_Include_Suffix__c',
       'Suppress_From_Reports__c', 'adpdx_Seminarian_Student_Debt__c',
       'adpdx_Seminarian_Medical_Benefits__c', 'Send_Group_Mail_and_Email__c',
       'Birthdate', 'mbfc__Place_of_Birth__c', 'Foreign_Born__c',
       'Foreign_Citizenship__c', 'Immigration_Status__c',
       'Passport_Visa_Expiration_Date__c',
       'adpdx_Accepted_to_Formation_Date__c', 'adpdx_Candidacy_Date__c',
       'adpdx_Formation_Withdrawn_Date__c', 'adpdx_Formation_Deferred_Date__c',
  

## Load


In [264]:
df_contact_staging['Archdpdx_Job_Id__c'] = curr_job_id

In [265]:
# generate CSV for manual loading
df_contact_staging.to_csv(f'/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/staging/df_contacts_staging.csv', encoding='utf-8-sig')
df_contact_staging.to_csv('staging_files/contacts_staging.csv', encoding='utf-8-sig')


In [266]:
# upsert Contact records into SF using Bulk api

from simple_salesforce.exceptions import SalesforceMalformedRequest

bulk_data = []
for row in df_contact_staging.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

try:
    # Attempt to upsert Contact records into SF using Bulk API
    contact_upsert = sf.bulk.Contact.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=200, use_serial=True)
    contact_upsert_results = pd.DataFrame(contact_upsert)
except SalesforceMalformedRequest as e:
    # If a SalesforceMalformedRequest error occurs, print the error message and response content
    print(f"SalesforceMalformedRequest error: {e}")
    print(f"Response content: {e.content}")

In [268]:
# Print upsert results to local file

keys = contact_upsert[0].keys()
with open('results_files/contact_results', 'w', newline='') as csv_file:
    writer = csv.DictWriter(csv_file, keys)
    writer.writeheader()
    writer.writerows(contact_upsert)


# CONTACT > SPOUSES

#TODO: Contact Spouses migration

# CONTACTS > PHOTOS

#TODO: Contact Photos

# CONTACT > REGISTER ENTRIES


In [170]:
import pandas as pd

# Load CSV
df = (pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/People.csv')
               .rename(columns=lambda x: x.replace(' ', '_')) # Remove whitespace in column names
               .drop(index=0) # Drops the extra row that replicates the labels
)

df

Record_Number                Common_Name                 Sort_Name  \
1             2766      Rev. Stephen Abaukaka  abaukaka stephen ozovehe   
2             2337        Mr. Rogelio Acevedo           acevedo rogelio   
3             3244           Mr. Sean Ackroyd              ackroyd sean   
4             3295          Ms. Sherril Acton             acton sherril   
5             2164          Ms. Barbara Adams             adams barbara   
...            ...                        ...                       ...   
3012          1670         Ms. Jenny Zomerdyk            zomerdyk jenny   
3013          2755  Br. Daniel Zorrilla, MSpS           zorrilla daniel   
3014          1962              Ms. Kim Zuber                 zuber kim   
3015          2202           Ms. Agnes Zueger              zueger agnes   
3016          1866          Ms. Laurie Zupsic             zupsic laurie   

        Type(s)    Clergy_Status Religious_Status   Login_ID  \
1        Priest  Transferred Out              NaN   sabukaka   
2         Staff              NaN              NaN        NaN   
3         Staff              NaN              NaN        NaN   
4         Staff              NaN              NaN        NaN   
5         Staff              NaN              NaN        NaN   
...         ...              ...              ...        ...   
3012      Staff              NaN              NaN        NaN   
3013  Religious              NaN           Active  dzorrilla   
3014      Staff              NaN              NaN        NaN   
3015      Staff              NaN              NaN        NaN   
3016      Staff              NaN              NaN        NaN   

                                               Password  \
1     def2a990be60a7998b1ed7c820101f3bd02d33b8992518...   
2                                                   NaN   
3                                                   NaN   
4                                                   NaN   
5                                                   NaN   
...                                                 ...   
3012                                                NaN   
3013  391eedf7c936f63d3d0a7d9ea7e506a84709662fd31ba9...   
3014                                                NaN   
3015                                                NaN   
3016                                                NaN   

     Password_Must_be_Changed Access_Permission  ... CARA_Ethnicity  \
1                         Yes               NaN  ...            NaN   
2                         NaN               NaN  ...            NaN   
3                         NaN               NaN  ...            NaN   
4                         NaN               NaN  ...            NaN   
5                         NaN               NaN  ...            NaN   
...                       ...               ...  ...            ...   
3012                      NaN               NaN  ...            NaN   
3013                      Yes               NaN  ...            NaN   
3014                      NaN               NaN  ...            NaN   
3015                      NaN               NaN  ...            NaN   
3016                      NaN               NaN  ...            NaN   

     Seminarian_Status Other_Diaconal_Ministry Spiritual_Director_Authorized  \
1                  NaN                     NaN                           NaN   
2                  NaN                     NaN                           NaN   
3                  NaN                     NaN                           NaN   
4                  NaN                     NaN                           NaN   
5                  NaN                     NaN                           NaN   
...                ...                     ...                           ...   
3012               NaN                     NaN                           NaN   
3013               NaN                     NaN                           NaN   
3014               NaN                     NaN       

In [171]:
# Import all Contact fields that actually map to Register Entry records

import pandas as pd

# Define the structure of your column sets with correct attribute names
column_sets = [
    {'date': 'Baptism_Date', 'place': 'Place_of_Baptism', 'notation_type': 'Proof of Baptism'},
    {'date': 'Confirmation_Date', 'place': 'Place_of_Confirmation', 'notation_type': 'Notice of Confirmation'},
    {'date': 'Received_Date', 'place': 'Parish_of_Record', 'notation_type': 'Notice of Profession of Faith'},
    {'date': 'Marriage_Date', 'place': 'Place_of_Marriage', 'notation_type': 'Notice of Matrimony'},
    {'date': 'Diaconal_Ordination_Date', 'place': 'Diaconal_Ordination_Place', 'prelate': 'Diaconate_Ordination_Prelate', 'notation_type': 'Notice of Holy Orders', 'ordination_type': 'Diaconate'},
    {'date': 'Presbyteral_Ordination_Date', 'place': 'Presbyteral_Ordination_Place', 'prelate': 'Presbyteral_Ordination_Prelate', 'notation_type': 'Notice of Holy Orders', 'ordination_type': 'Presbyteral'},
    {'date': 'Episcopal_Ordination_Date', 'place': 'Episcopal_Ordination_Place', 'prelate': 'Episcopal_Ordination_Prelate', 'notation_type': 'Notice of Holy Orders', 'ordination_type': 'Episcopal'}
]

# New DataFrame for entries
register_entries = pd.DataFrame(columns=['RecordNumber', 'mbfc__Register_Entry_Type__c', 'mbfc__Type__c', 'mbfc__Notation_Type__c', 'mbfc__Ordination_Type__c', 'Date', 'Place', 'Prelate'])
new_entries = []  # List to store entries before final concatenation

# Processing rows
for row in df.itertuples():
    for column_set in column_sets:
        date_value = getattr(row, column_set['date'], None)
        if pd.notna(date_value):  # Check if date field is not NaN
            entry = {
                'RecordNumber': getattr(row, 'Record_Number', None),
                'Date': date_value,
                'Place': getattr(row, column_set['place'], None)
            }
            # Add Prelate if applicable
            if 'prelate' in column_set:
                entry['Prelate'] = getattr(row, column_set['prelate'], None)

            # Set 'mbfc__Register_Entry_Type__c', and conditionally add 'mbfc__Type__c' or 'mbfc__Notation_Type__c'
            if 'sacrament_type' in column_set:
                entry['mbfc__Type__c'] = column_set['sacrament_type']
                entry['mbfc__Register_Entry_Type__c'] = 'Sacrament'
            if 'notation_type' in column_set:
                entry['mbfc__Notation_Type__c'] = column_set['notation_type']
                entry['mbfc__Register_Entry_Type__c'] = 'Notation'

            # Handle ordination type specific updates
            if 'ordination_type' in column_set:
                entry['mbfc__Ordination_Type__c'] = column_set['ordination_type']

            new_entries.append(entry)
    
    # Add entries for 'Reader Date'
    reader_date = getattr(row, 'Reader_Date', None)
    if pd.notna(reader_date):
        entry = {
            'RecordNumber': getattr(row, 'Record_Number', None),
            'Date': reader_date,
            'mbfc__Notation_Type__c': 'Notice of Holy Orders',
            'mbfc__Ordination_Type__c': 'Minor Order: Reader',
            'mbfc__Register_Entry_Type__c': 'Notation'
        }
        new_entries.append(entry)
    
    # Add entries for 'Acolyte Date'
    acolyte_date = getattr(row, 'Acolyte_Date', None)
    if pd.notna(acolyte_date):
        entry = {
            'RecordNumber': getattr(row, 'Record_Number', None),
            'Date': acolyte_date,
            'mbfc__Notation_Type__c': 'Notice of Holy Orders',
            'mbfc__Ordination_Type__c': 'Minor Order: Acolyte',
            'mbfc__Register_Entry_Type__c': 'Notation'
        }
        new_entries.append(entry)

# Concatenate all new entries to the DataFrame at once
if new_entries:
    register_entries = pd.concat([register_entries, pd.DataFrame(new_entries)], ignore_index=True)

print(f"Total records added: {len(register_entries)}")

# Optionally, save the new DataFrame to a CSV
register_entries.to_csv('Register_Entries.csv', index=False)

# Display the DataFrame
register_entries.sample(10)


Total records added: 1872


RecordNumber mbfc__Register_Entry_Type__c mbfc__Type__c  \
154          3109                     Notation           NaN   
1228         2098                     Notation           NaN   
31            287                     Notation           NaN   
405           474                     Notation           NaN   
991           129                     Notation           NaN   
41            179                     Notation           NaN   
10           1584                     Notation           NaN   
1671           39                     Notation           NaN   
1220         2092                     Notation           NaN   
844           535                     Notation           NaN   

     mbfc__Notation_Type__c mbfc__Ordination_Type__c        Date  \
154     Notice of Matrimony                      NaN  1994-06-18   
1228  Notice of Holy Orders      Minor Order: Reader  2020-01-09   
31      Notice of Matrimony                      NaN  1965-12-27   
405   Notice of Holy Orders      Minor Order: Reader  2019-03-23   
991     Notice of Matrimony                      NaN  1989-02-04   
41      Notice of Matrimony                      NaN  1988-10-01   
10         Proof of Baptism                      NaN  1985-11-20   
1671    Notice of Matrimony                      NaN  1954-07-17   
1220    Notice of Matrimony                      NaN  1980-09-26   
844   Notice of Holy Orders              Presbyteral  2019-06-15   

                                                  Place  \
154                      St. Anthony Parish, Tigard, OR   
1228                                                NaN   
31                                                  NaN   
405                                                 NaN   
991                                                 NaN   
41                                                  NaN   
10                                 Moyo Catholic Parish   
1671                                                NaN   
1220   St. Francis Xavier Parish, Bali Nyonga, Cameroon   
844   Cathedral of the Immaculate Conception, Portla...   

                                          Prelate  
154                                           NaN  
1228                                          NaN  
31                                            NaN  
405                                           NaN  
991                                           NaN  
41                                            NaN  
10                                            NaN  
1671                                          NaN  
1220                                          NaN  
844   Most Rev. Alexander K. Sample, J.C.L., D.D.

In [172]:
from nameparser import HumanName
from nameparser.config import CONSTANTS

# Add dataset-specific Titles and Suffix constants for parsing
CONSTANTS.titles.add('Very', 'Rev.', 'Very Rev.', 'Sr.', 'Most Rev.')
CONSTANTS.suffix_acronyms.add('FRS', 'J.C.L.', 'J.C.L., D.D.', 'D.D.', 'OMI', 'OSA', 'OCD', 'OP', 'OC', 'FSE', 'OMV', 'SDB', 'SM', 'SFX', 'SP', 'OP', 'O.S.M', 'SNJM', 'OSF', 'HMRF', 'DD', 'CSJP', 'SDD', 'BVM', 'BVM - President', 'SJ', 'SL', 'IX', 'SSJ', 'J.C.L.', 'J.C.L', 'OFM', 'MSpS', 'Fco.' )


def parse_name(name):
    if pd.isna(name):  # Checks if the name is NaN or None
        return {
            'Salutation': '',
            'FirstName': '',
            'MiddleName': '',
            'LastName': '',
            'Suffix': ''
        }
    else:
        name = HumanName(name)
        return {
            'Salutation': name.title,
            'FirstName': name.first,
            'MiddleName': name.middle,
            'LastName': name.last,
            'Suffix': name.suffix
        }

# Apply the parsing function only where 'Prelate' exists and is not NaN
for entry in new_entries:
    if 'Prelate' in entry and pd.notna(entry['Prelate']):
        parsed_name = parse_name(entry['Prelate'])
        entry.update(parsed_name)

# Ensure the DataFrame creation from new_entries includes checks for existence of keys:
register_entries = pd.DataFrame(new_entries)
if 'Prelate' in register_entries.columns:
    register_entries['Salutation'] = register_entries['Prelate'].apply(lambda x: parse_name(x)['Salutation'] if pd.notna(x) else '')
    register_entries['FirstName'] = register_entries['Prelate'].apply(lambda x: parse_name(x)['FirstName'] if pd.notna(x) else '')
    register_entries['MiddleName'] = register_entries['Prelate'].apply(lambda x: parse_name(x)['MiddleName'] if pd.notna(x) else '')
    register_entries['LastName'] = register_entries['Prelate'].apply(lambda x: parse_name(x)['LastName'] if pd.notna(x) else '')
    register_entries['Suffix'] = register_entries['Prelate'].apply(lambda x: parse_name(x)['Suffix'] if pd.notna(x) else '')


# Display the DataFrame
print(f"Total records added: {len(register_entries)}")
register_entries.sample(10)



Total records added: 1872


RecordNumber        Date                                      Place  \
416           164  1996-08-03                                        NaN   
172           320  2004-12-18                                        NaN   
505           202  1995-11-30                                        NaN   
882           301  1999-02-13                                        NaN   
826           534  2015-01-11                                        NaN   
816          2080  1978-04-02                                        NaN   
1188          655  1939-03-21                               Portland, Or   
449           685  1958-05-24                               Portland, OR   
1553          250  1999-12-18  St. Louis Catholic Church, New Orleans LA   
1634          659  1965-05-06                                        NaN   

                         Prelate mbfc__Notation_Type__c  \
416                          NaN  Notice of Holy Orders   
172                          NaN  Notice of Holy Orders   
505                          NaN  Notice of Holy Orders   
882                          NaN    Notice of Matrimony   
826                          NaN  Notice of Holy Orders   
816                          NaN    Notice of Matrimony   
1188                         NaN       Proof of Baptism   
449   Most Rev. Edward D. Howard  Notice of Holy Orders   
1553                        None  Notice of Holy Orders   
1634                         NaN  Notice of Holy Orders   

     mbfc__Register_Entry_Type__c mbfc__Ordination_Type__c Salutation  \
416                      Notation     Minor Order: Acolyte              
172                      Notation      Minor Order: Reader              
505                      Notation     Minor Order: Acolyte              
882                      Notation                      NaN              
826                      Notation      Minor Order: Reader              
816                      Notation                      NaN              
1188                     Notation                      NaN              
449                      Notation              Presbyteral  Most Rev.   
1553                     Notation                Diaconate              
1634                     Notation     Minor Order: Acolyte              

     FirstName MiddleName LastName Suffix  
416                                        
172                                        
505                                        
882                                        
826                                        
816                                        
1188                                       
449     Edward         D.   Howard         
1553                                       
1634

In [173]:
# @title Query Salesforce for existing contacts and create a dictionary for mapping

from simple_salesforce import Salesforce

query = """
SELECT Id, Archdpdx_Migration_Id__c
FROM Contact
"""
result = sf.query_all(query)
contact_map = {rec['Archdpdx_Migration_Id__c']: rec['Id'] for rec in result['records']}


In [174]:
# Get RecordTypeId for Contact.Priest

priest_contact_recordtype_id = df_sf_recordTypes.loc[
    (df_sf_recordTypes['DeveloperName'] == 'Priest') & (df_sf_recordTypes['SobjectType'] == 'Contact'),
    'Id'
    ].iloc[0]  # Use .iloc[0] to get the first item if you're expecting exactly one match


In [175]:
# Query for Contacts by Names and Create New Contacts

from simple_salesforce import SFType, SalesforceResourceNotFound

contact = SFType('Contact', sf.session_id, sf.sf_instance)
for index, row in register_entries.iterrows():
    first_name, last_name = row.get('FirstName'), row.get('LastName')

    if pd.isna(first_name) or pd.isna(last_name) or first_name.strip() == '' or last_name.strip() == '':
        # If either first name or last name is missing or empty, skip this row or handle as needed
        print(f"Skipping row {index} due to missing name information.")
        continue

    try:
        # Search for contact by First and Last Name
        query = f"SELECT Id FROM Contact WHERE FirstName = '{first_name}' AND LastName = '{last_name}'"
        result = sf.query(query)
        if result['totalSize'] > 0:
            contact_id = result['records'][0]['Id']
        else:
            # Create a new contact if no match found
            new_contact = {
                'FirstName': first_name,
                'LastName': last_name,
                'Archdpdx_Job_Id__c': curr_job_id,
                'RecordTypeId': priest_contact_recordtype_id
            }
            create_result = contact.create(new_contact)
            contact_id = create_result['id']

        # Update DataFrame with the Salesforce Contact ID
        register_entries.at[index, 'mbfc__Celebrant__c'] = contact_id

    except SalesforceException as e:
        print(f"Error processing row {index}: {e}")



Skipping row 2 due to missing name information.
Skipping row 3 due to missing name information.
Skipping row 4 due to missing name information.
Skipping row 5 due to missing name information.
Skipping row 6 due to missing name information.
Skipping row 8 due to missing name information.
Skipping row 9 due to missing name information.
Skipping row 10 due to missing name information.
Skipping row 11 due to missing name information.
Skipping row 12 due to missing name information.
Skipping row 13 due to missing name information.
Skipping row 14 due to missing name information.
Skipping row 15 due to missing name information.
Skipping row 16 due to missing name information.
Skipping row 17 due to missing name information.
Skipping row 19 due to missing name information.
Skipping row 20 due to missing name information.
Skipping row 21 due to missing name information.
Skipping row 22 due to missing name information.
Skipping row 24 due to missing name information.
Skipping row 25 due to miss

In [176]:
# @title Map Contact IDs to Register Entries

register_entries_2 = register_entries

register_entries_2['mbfc__Contact__c'] = register_entries['RecordNumber'].map(contact_map)


In [177]:
# @title Append Job_Id__c
register_entries_2['Archdpdx_Job_Id__c'] = curr_job_id

## Generate an External ID


In [178]:
def create_external_id(row):
    record_number = str(row['RecordNumber']).replace(' ', '').replace('-', '')
    entry_type = str(row['mbfc__Register_Entry_Type__c']).replace(' ', '').replace('-', '')

    # Check whether to use Type or Notation Type based on what's available
    if 'mbfc__Type__c' in row and not pd.isna(row['mbfc__Type__c']):
        type_field = str(row['mbfc__Type__c']).replace(' ', '').replace('-', '')
    elif 'mbfc__Notation_Type__c' in row and not pd.isna(row['mbfc__Notation_Type__c']):
        type_field = str(row['mbfc__Notation_Type__c']).replace(' ', '').replace('-', '') + str(row['mbfc__Ordination_Type__c']).replace(' ', '').replace('-', '')
    else:
        type_field = 'Unknown'

    return f"{record_number}_{entry_type}_{type_field}"

In [179]:
# Assuming your DataFrame is named `register_entries`
register_entries_2['Archdpdx_Migration_Id__c'] = register_entries.apply(create_external_id, axis=1)

if register_entries['Archdpdx_Migration_Id__c'].duplicated().any():
    print("Warning: There are duplicate external IDs.")
    # Optionally, show the duplicates
    duplicates = register_entries[register_entries['external_id'].duplicated(keep=False)]
    print(duplicates)
else:
    print("All external IDs are unique.")


All external IDs are unique.


In [180]:
# Drop unnecessary columns:
register_entries_2.drop(['RecordNumber', 'Prelate', 'Salutation', 'FirstName', 'MiddleName', 'LastName', 'Suffix'], axis=1, inplace=True)

In [181]:
register_entries_staging = register_entries_2

In [182]:
# Remove all NaN values:
register_entries_staging.fillna('', inplace=True)

# Rename columns
register_entries_staging = register_entries_staging.rename(columns={
    'Place': 'Location_text__c',
    'Date': 'mbfc__Event_Date__c'
})


In [183]:
# Upsert Register Entry Records

bulk_data = []
for row in register_entries_staging.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

# Keep the batch <100 as I've been getting an exceptionCode: 'InvalidBatch', 'exceptionMessage': 'Records not processed'
reg_entry_upsert = sf.bulk.mbfc__Sacrament__c.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
reg_entry_upsert_results = pd.DataFrame(reg_entry_upsert)

KeyboardInterrupt: 

In [ ]:
# Print upsert results to local file

keys = reg_entry_upsert[0].keys()

with open('results_files/register_entry_results', 'w', newline='') as csv_file:
    writer = csv.DictWriter(csv_file, keys)
    writer.writeheader()
    writer.writerows(reg_entry_upsert)

# CONTACT > AFFILIATIONS


In [ ]:
# Function to create a unique ID based on Person's Name + completion date + affiliation type
def create_unique_id(row):
    # Concatenate the three fields with mbfc__Person__c at the front
    combined = f"{row['mbfc__Person__c']}{row['mbfc__Completion_Date__c']}{row['mbfc__Affiliation__c']}"
    # Remove unwanted characters and convert to lowercase
    clean_id = ''.join(combined.split()).replace('-', '').replace('.', '').lower()
    # Limit the string to 50 characters
    return clean_id[:50]

## Education Affiliations

This section takes multiple sets of columns (all related to a person's education) from the Contacts table, and combines them into a single set of columns in a new dataframe for insertion into Salesforce as Affiliation records.


In [ ]:
# Parse and stage Education Affiliation records
import pandas as pd
from functools import lru_cache

# Load CSV
df = (pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/People.csv')
               .rename(columns=lambda x: x.replace(' ', '_')) # Remove whitespace in column names
               .drop(index=0) # Drops the extra row that replicates the labels
)


# Define the structure of your column sets with correct attribute names
degree_sets = [
    {'year': 'Bachelor_Degree_Year', 'type': 'Bachelor_Degree_Type', 'institution': 'Bachelor_Degree_Institution'},
    {'year': 'Graduate_1_Degree_Year', 'type': 'Graduate_1_Degree_Type', 'institution': 'Graduate_1_Degree_Institution'},
    {'year': 'Graduate_2_Degree_Year', 'type': 'Graduate_2_Degree_Type', 'institution': 'Graduate_2_Degree_Institution'},
    {'year': 'Graduate_3_Degree_Year', 'type': 'Graduate_3_Degree_Type', 'institution': 'Graduate_3_Degree_Institution'},
    {'year': 'Graduate_4_Degree_Year', 'type': 'Graduate_4_Degree_Type', 'institution': 'Graduate_4_Degree_Institution'}
]

# Query for the Record Type ID for 'Organization'
record_type_result = sf.query("SELECT Id FROM RecordType WHERE SobjectType = 'Account' AND DeveloperName = 'Organization'")
organization_record_type_id = record_type_result['records'][0]['Id'] if record_type_result['records'] else None

# Initialize the DataFrame for the staging table
education_staging = pd.DataFrame()

# Function to check and create institution account
@lru_cache(maxsize=None)
def get_or_create_institution_account(institution_name):
    if pd.isna(institution_name):
        return None  # Return None or handle as appropriate if institution name is NaN

    # Query Salesforce to find the institution
    query = f"SELECT Id, Name FROM Account WHERE Name = '{institution_name}' LIMIT 1"
    results = sf.query(query)
    
    # If exists, return the ID
    if results['records']:
        return results['records'][0]['Id']
    else:
        # Ensure no NaN values are sent to Salesforce
        account_data = {
            'Name': institution_name if pd.notna(institution_name) else "Default Name",  # Provide a default if NaN
            'RecordTypeId': organization_record_type_id,
            'Organization_Type__c': 'School'
        }
        # Remove keys with None values to avoid JSON serialization issues
        account_data = {k: v for k, v in account_data.items() if v is not None}
        
        new_account = sf.Account.create(account_data)
        return new_account['id']

# Get Contact record ID from Salesforce
@lru_cache(maxsize=None)
def get_contact_id_by_record_number(record_number):
    if pd.isna(record_number):
        return None
    query = f"SELECT Id FROM Contact WHERE Archdpdx_Migration_Id__c = '{record_number}'"
    results = sf.query(query)
    if results['records']:
        return results['records'][0]['Id']
    return None


# Initialize an empty list to collect DataFrames or dictionaries
new_entries = []

# Process each row and each degree set
for index, row in df.iterrows():
    for degree_set in degree_sets:
        year = row[degree_set['year']]
        if pd.notna(year):  # Only proceed if the year column is not NaN
            formatted_year = f"{int(year)}-01-01"  # Convert year to YYYY-MM-DD format
            institution_name = row[degree_set['institution']]
            account_id = get_or_create_institution_account(institution_name)
            contact_id = get_contact_id_by_record_number(row['Record_Number'])
            
            # Create a record for the staging table
            affiliation_record = {
                'mbfc__Person__c': contact_id,
                'mbfc__Completion_Date__c': formatted_year,
                'mbfc__Context__c': account_id,
                'mbfc__Category__c': 'Education (non-degree)',
                'mbfc__Affiliation__c': row[degree_set['type']]
                # 'Institution_Name': institution_name
            }
            new_entries.append(affiliation_record)

# Convert all collected records to a DataFrame in one go
education_staging = pd.DataFrame(new_entries)


#FIXME: There are 4 rows where no INSTITUTION is listed. This makes it impossible to import an Affiliation record. Need to figure out how to handle this with Client. 
#FIXME: There are about 15 rows where no DEGREE is listed. This makes it impossible to import an Affiliation record. Need to figure out how to handle this with Client. 

In [ ]:
# Apply the function to each row and create a new column with the unique ID
education_staging['Archdpdx_Migration_Id__c'] = education_staging.apply(create_unique_id, axis=1)

# Check the first few rows to verify the new column
education_staging.head()

mbfc__Person__c mbfc__Completion_Date__c    mbfc__Context__c  \
0  003Dx00000m0Oa7IAE               1996-01-01                None   
1  003Dx00000m0Oa7IAE               2013-01-01  001Dx00001FaYqrIAF   
2  003Dx00000m0OXKIA2               1976-01-01  001Dx00001FaYqwIAF   
3  003Dx00000m0OXKIA2               1980-01-01  001Dx00001FaYr1IAF   
4  003Dx00000m0OajIAE               2004-01-01  001Dx00001FaYr6IAF   

        mbfc__Category__c  mbfc__Affiliation__c  \
0  Education (non-degree)              Theology   
1  Education (non-degree)   MA Pastoral Studies   
2  Education (non-degree)       BA Liberal Arts   
3  Education (non-degree)                M.Div.   
4  Education (non-degree)  Bachelor, Philosophy   

                        Archdpdx_Migration_Id__c  
0             003dx00000m0oa7iae19960101theology  
1    003dx00000m0oa7iae20130101mapastoralstudies  
2        003dx00000m0oxkia219760101baliberalarts  
3                 003dx00000m0oxkia219800101mdiv  
4  003dx00000m0oajiae20040101bachelor,philosophy

In [ ]:
# Fill any NaN values
education_staging = education_staging.fillna('')

In [ ]:
# Save the staging table to CSV
education_staging.to_csv('staging_files/education_staging.csv', index=False)


In [ ]:
# Upsert Education Affiliation records

bulk_data = []
for row in education_staging.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

# Keep the batch <100 as I've been getting an exceptionCode: 'InvalidBatch', 'exceptionMessage': 'Records not processed'
education_affil_upsert = sf.bulk.mbfc__Placement__c.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
education_affil_upsert_results = pd.DataFrame(education_affil_upsert)

In [ ]:
education_affil_upsert_results.to_csv('results_files/education_affil_upsert_results')

#FIXME: A number of Education Affiliation records are missing either an Affiliation title or a Context

## Ecclesial Affiliations

This section handles Contact table fields that map to Affiliation records with record type 'Ecclesial Affiliation'.

These Ecclesial Affiliations can be subcategorized by the 'contexts' to which the Affiliation records is related: 

| Affiliation           | Context                   | Completion Date           |
------------------------|---------------------------|---------------------------|
| First Vows            | Religious Order           | Date of First Vows        |
| Final Vows            | Religious Order           | Date of Final Vows        |
| Incardination         | Incardinated from Diocese | Incardinated From Date    |
| Faculties (Type)      | Local Diocese             | Faculties Granted Date    |
| Faculties (Restricted)| Local Diocese             | Faculties Restricted Date |
| Faculties (Withdrawn) | Local Diocese             | Faculties Withdrawn Date  |
| Excardinated          | Excardinated To Diocese   | Excardinated To Date      |


FIXME: There are a number of rows where a Faculties Granted is missing a date, and conversely, where there is a Faculties Granted Date but no description of the Faculties granted. This is a problem, because the application requires a date for when Faculties were granted.

In [ ]:
import pandas as pd
from functools import lru_cache
from simple_salesforce import Salesforce

# Load CSV
df = (pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/People.csv')
               .rename(columns=lambda x: x.replace(' ', '_')) # Remove whitespace in column names
               .drop(index=0) # Drops the extra row that replicates the labels
)

# Define the structure of your column sets with correct attribute names
column_sets = [
    {'year': 'Incardinated_From_Date', 'context': 'Incardinated_From_Diocese'},
    {'year': 'Excardinated_To_Date', 'context': 'Excardinated_To_Diocese'},
    {'year': 'Faculties_Granted_Date', 'affiliation': 'Faculties'},
    {'year': 'Faculties_Restricted_Date'},
    {'year': 'Faculties_Withdrawn_Date'},
]

# Query for the Record Type IDs
record_type_query = "SELECT Id, DeveloperName FROM RecordType WHERE SobjectType = 'Account' AND DeveloperName IN ('Church', 'Religious')"
record_type_result = sf.query(record_type_query)
record_type_ids = {record['DeveloperName']: record['Id'] for record in record_type_result['records']}

church_record_type_id = record_type_ids.get('Church')
religious_record_type_id = record_type_ids.get('Religious')

# Query for the Record Type ID for 'Ecclesial Affiliation' for mbfc__Placement__c object
record_type_query = "SELECT Id FROM RecordType WHERE SobjectType = 'mbfc__Placement__c' AND DeveloperName = 'Ecclesial_Affiliation' LIMIT 1"
record_type_result = sf.query(record_type_query)
ecclesial_affiliation_record_type_id = record_type_result['records'][0]['Id'] if record_type_result['records'] else None

# Initialize the DataFrame for the staging table
ecclesial_affiliation_staging = pd.DataFrame()

# Function to check and create institution account
@lru_cache(maxsize=None)
def get_or_create_church_account(context):
    if pd.isna(context):
        return None  # Return None or handle as appropriate if institution name is NaN

    # Query Salesforce to find the institution
    query = f"SELECT Id, Name FROM Account WHERE Name = '{context}' LIMIT 1"
    results = sf.query(query)
    
    # If exists, return the ID
    if results['records']:
        return results['records'][0]['Id']
    else:
        # Ensure no NaN values are sent to Salesforce
        if 'Diocese' in context or 'Archdiocese' in context:
            account_data = {
                'Name': context if pd.notna(context) else "Church Name Missing",  # Provide a default if NaN
                'RecordTypeId': church_record_type_id,
                'mbfc__Church_Type__c': 'Diocese'
            }
        else:
            account_data = {
                'Name': context if pd.notna(context) else "Religious Name Missing",  # Provide a default if NaN
                'RecordTypeId': religious_record_type_id
            }

        # Remove keys with None values to avoid JSON serialization issues
        account_data = {k: v for k, v in account_data.items() if v is not None}
        
        new_account = sf.Account.create(account_data)
        return new_account['id']

# Get Contact record ID from Salesforce
@lru_cache(maxsize=None)
def get_contact_id_by_record_number(record_number):
    if pd.isna(record_number):
        return None
    query = f"SELECT Id FROM Contact WHERE Archdpdx_Migration_Id__c = '{record_number}'"
    results = sf.query(query)
    if results['records']:
        return results['records'][0]['Id']
    return None

# Initialize an empty list to collect DataFrames or dictionaries
new_entries = []

# Process each row and each degree set
for index, row in df.iterrows():
    for col_set in column_sets:
        date = row[col_set['year']]
        if pd.notna(date):  # Only proceed if the year column is not NaN
            context = row.get(col_set.get('context'), None)
            account_id = get_or_create_church_account(context)
            contact_id = get_contact_id_by_record_number(row['Record_Number'])
            
            # Determine the mbfc__Affiliation__c value
            if 'Incardinated_From_Date' in col_set['year']:
                affiliation = 'Incardinated'
            elif 'Excardinated_To_Date' in col_set['year']:
                affiliation = 'Excardinated'
            elif 'Faculties_Granted_Date' in col_set['year']:
                faculties_value = row.get(col_set.get('affiliation', ''))
                if pd.isna(faculties_value):
                    affiliation = 'Faculties'
                else:
                    affiliation = f"Faculties ({faculties_value})"
                account_id = diocesan_account_id  # Override account ID for faculties
            elif 'Faculties_Restricted_Date' in col_set['year']:
                affiliation = 'Faculties (Restricted)'
                account_id = diocesan_account_id  # Override account ID for faculties
            elif 'Faculties_Withdrawn_Date' in col_set['year']:
                affiliation = 'Faculties (Withdrawn)'
                account_id = diocesan_account_id  # Override account ID for faculties
            elif 'Date_of_First_Vows' in col_set['year']:
                affiliation = 'First Vows'
            elif 'Date_of_Final_Vows' in col_set['year']:
                affiliation = 'Final Vows'
            else:
                affiliation = row.get(col_set.get('affiliation', ''), None)
            
            # Create a record for the staging table
            affiliation_record = {
                'RecordTypeId': ecclesial_affiliation_record_type_id,
                'mbfc__Person__c': contact_id,
                'mbfc__Completion_Date__c': date,
                'mbfc__Context__c': account_id,
                'mbfc__Category__c': 'Ecclesial Affiliations',
                'mbfc__Affiliation__c': affiliation
            }
            new_entries.append(affiliation_record)

# Convert all collected records to a DataFrame in one go
ecclesial_affiliations_staging = pd.DataFrame(new_entries)



In [ ]:
# Apply the function to each row and create a new column with the unique ID
ecclesial_affiliations_staging['Archdpdx_Migration_Id__c'] = ecclesial_affiliations_staging.apply(create_unique_id, axis=1)

# Check for duplicates
ecclesial_affiliations_staging['Archdpdx_Migration_Id__c'].duplicated().value_counts()

False    529
Name: Archdpdx_Migration_Id__c, dtype: int64

In [ ]:

# Save the new DataFrame to a CSV
ecclesial_affiliations_staging.to_csv('staging_files/Ecclesial_Affiliations_Staging.csv', index=False, encoding='utf-8-sig')

# Display the DataFrame
ecclesial_affiliations_staging.sample(10)

RecordTypeId     mbfc__Person__c mbfc__Completion_Date__c  \
209  012Dx0000007yIOIAY  003Dx00000m0OvoIAE               2023-06-03   
353  012Dx0000007yIOIAY  003Dx00000m0P7gIAE               2012-09-12   
207  012Dx0000007yIOIAY  003Dx00000m0OvlIAE               2015-06-08   
523  012Dx0000007yIOIAY  003Dx00000m0PM1IAM               2002-10-15   
487  012Dx0000007yIOIAY  003Dx00000m0PJeIAM               1993-11-05   
381  012Dx0000007yIOIAY  003Dx00000m0PA4IAM               2006-12-09   
65   012Dx0000007yIOIAY  003Dx00000m0OgtIAE               2008-10-25   
344  012Dx0000007yIOIAY  003Dx00000m0P72IAE               2005-06-11   
400  012Dx0000007yIOIAY  003Dx00000m0PCKIA2               2003-10-01   
461  012Dx0000007yIOIAY  003Dx00000m0PHCIA2               2018-11-12   

       mbfc__Context__c       mbfc__Category__c      mbfc__Affiliation__c  \
209  001Dx00001CwMTQIA3  Ecclesial Affiliations       Faculties (General)   
353  001Dx00001CwMTQIA3  Ecclesial Affiliations      Faculties (Diaconal)   
207  001Dx00001CwMTQIA3  Ecclesial Affiliations    Faculties (Restricted)   
523  001Dx00001CwMTQIA3  Ecclesial Affiliations  Faculties (Confessional)   
487  001Dx00001CwMTQIA3  Ecclesial Affiliations      Faculties (Diaconal)   
381  001Dx00001CwMTQIA3  Ecclesial Affiliations      Faculties (Diaconal)   
65   001Dx00001CwMTQIA3  Ecclesial Affiliations      Faculties (Diaconal)   
344  001Dx00001CwMTQIA3  Ecclesial Affiliations       Faculties (General)   
400  001Dx00001CwMTQIA3  Ecclesial Affiliations                 Faculties   
461  001Dx00001CwMTQIA3  Ecclesial Affiliations       Faculties (General)   

                              Archdpdx_Migration_Id__c  
209       003dx00000m0ovoiae20230603faculties(general)  
353      003dx00000m0p7giae20120912faculties(diaconal)  
207    003dx00000m0ovliae20150608faculties(restricted)  
523  003dx00000m0pm1iam20021015faculties(confessional)  
487      003dx00000m0pjeiam19931105faculties(diaconal)  
381      003dx00000m0pa4iam20061209faculties(diaconal)  
65       003dx00000m0ogtiae20081025faculties(diaconal)  
344       003dx00000m0p72iae20050611faculties(general)  
400                003dx00000m0pckia220031001faculties  
461       003dx00000m0phcia220181112faculties(general)

In [ ]:
# Upsert Ecclesial Affiliation records

bulk_data = []
for row in ecclesial_affiliations_staging.itertuples(index=False):
    d = row._asdict()
    # del d['Index']
    bulk_data.append(d)

# Keep the batch <100 as I've been getting an exceptionCode: 'InvalidBatch', 'exceptionMessage': 'Records not processed'
ecclesial_affil_upsert = sf.bulk.mbfc__Placement__c.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=100, use_serial=False)
ecclesial_affil_upsert_results = pd.DataFrame(ecclesial_affil_upsert)

In [ ]:
ecclesial_affil_upsert_results.to_csv('results_files/ecclesial_affil_upsert_results') 

#FIXME: Handful of Ecclesial Affil records with error: [{'statusCode': 'FIELD_CUSTOM_VALIDATION_EXCEPTION', 'message': 'Context is required', 'fields': []}]"

# AFFILIATIONS


In [ ]:
# @title Import Assignments.csv

import pandas as pd

# No longer needed...
# Organization_mapping = {
#     'Offices': 'Organization',
#     'Parishes': 'Church',
#     'RelCommunities': 'Religious',
#     'Schools': 'School',
#     'Vicariates': 'Deanery',
#     'NewmanCenters': 'Organization'
# }

df_affiliations = (
    pd.read_csv('/Users/matthewmartin/Library/CloudStorage/GoogleDrive-matt@meribahflow.com/Shared drives/Clients/ADPDX (Portland)/Data/Clergy DB/reports from clergypdx/Assignments (1).csv')
    .set_index('Record Number', verify_integrity=True)
    .drop(index='recNum', errors='ignore')  # Added errors='ignore' to prevent errors if 'recNum' does not exist
    .drop(columns=['Historic Name'], errors='ignore')  # Added errors='ignore' for the same reason
    .rename(columns=lambda x: x.replace(' ', '_'))  # Remove whitespace in column names
    .assign(Account_Ext_Id=lambda df: df['Organization_Table_Name'] + '_' + df['Organization_Table_Link'])
    .assign(mbfc__Person__r=lambda df: df['Assigned_Person'].apply(lambda x: {'Archdpdx_Migration_Id__c': x}))
    .assign(mbfc__Context__r=lambda df: df['Account_Ext_Id'].apply(lambda x: {'Archdpdx_Migration_Id__c': x}))
    # .assign(mbfc__Use_Custom_Title__c= True)
    .assign(mbfc__Category__c= 'Any All')
    # .assign(Archdpdx_Migration_Id__c= df_affiliations.index)
    .drop(columns=[
        'Assigned_Person'
        ,'Organization_Table_Name'
        ,'Organization_Table_Link'
        ,'Projected_Term_End_Date'
        ,'Term_Number'
        ,'Leave_Type' # Leave out 'Leave_Type' until mapped properly
        ])
    .rename(columns={
        'Duty_Load': 'Duty_Load__c',
        'Start_Date': 'mbfc__Start_Date__c',
        'End_Date': 'mbfc__Completion_Date__c',
        'Assignment_Title': 'mbfc__Affiliation__c',
        'Archdiocesan_Assignment': 'ADPDX_Archdiocesan_Assignment__c',
    })
    .replace({'ADPDX_Archdiocesan_Assignment__c': {'Yes': True, 'No': False, None: False}})
    .fillna('')
)

# Display a sample of the DataFrame to check the new structure
df_affiliations.sample(10)



mbfc__Affiliation__c  \
Record Number                                              
3452                 Faith Formation Program Coordinator   
189                                               Pastor   
1014                                  Pastoral Associate   
718                                        Administrator   
2536                                      Student Deacon   
1251                Student, North America College, Rome   
45                                                Deacon   
508            Outreach and Special Projects Coordinator   
105                                               Deacon   
652                                             Chaplain   

               ADPDX_Archdiocesan_Assignment__c Duty_Load__c  \
Record Number                                                  
3452                                      False                
189                                        True                
1014                                      False                
718                                        True                
2536                                       True                
1251                                       True                
45                                         True                
508                                       False                
105                                        True                
652                                       False                

              mbfc__Start_Date__c mbfc__Completion_Date__c Account_Ext_Id  \
Record Number                                                               
3452                   2023-01-01                            Parishes_107   
189                    2016-07-01                             Parishes_93   
1014                                            1900-01-01    Parishes_62   
718                    2019-02-18               2020-06-30   Parishes_118   
2536                   2021-08-21               2022-05-31    Parishes_53   
1251                   2019-09-15               2020-06-15     Offices_21   
45                     2008-10-25                            Parishes_100   
508                                             2021-05-01      Offices_4   
105                    1999-08-27               2006-10-31   Parishes_147   
652                                             2018-01-01     Offices_18   

                                    mbfc__Person__r  \
Record Number                                         
3452           {'Archdpdx_Migration_Id__c': '3277'}   
189             {'Archdpdx_Migration_Id__c': '611'}   
1014           {'Archdpdx_Migration_Id__c': '1793'}   
718             {'Archdpdx_Migration_Id__c': '667'}   
2536           {'Archdpdx_Migration_Id__c': '2769'}   
1251            {'Archdpdx_Migration_Id__c': '534'}   
45               {'Archdpdx_Migration_Id__c': '95'}   
508            {'Archdpdx_Migration_Id__c': '1499'}   
105             {'Archdpdx_Migration_Id__c': '244'}   
652             {'Archdpdx_Migration_Id__c': '592'}   

                                           mbfc__Context__r mbfc__Category__c  
Record Number                                                                  
3452           {'Archdpdx_Migration_Id__c': 'Parishes_107'}           Any All  
189             {'Archdpdx_Migration_Id__c': 'Parishes_93'}           Any All  
1014            {'Archdpdx_Migration_Id__c': 'Parishes_62'}           Any All  
718            {'Archdpdx_Migration_Id__c': 'Parishes_118'}           Any All  
2536            {'Archdpdx_Migration_Id__c': 'Parishes_53'}           Any All  
1251             {'Archdpdx_Migration_Id__c': 'Offices_21'}           Any All  
45             {'Archdpdx_Migration_Id__c': 'Parishes_100'}           Any All  
508               {'Archdpdx_Migration_Id__c': 'Offices_4'}           Any All  
105            {'Archdpdx_Migration_Id__c': 'Parishes_147'}           Any All  
652              {'Archdpdx_Migration_Id__c': 'Offices_18'}           Any All

In [ ]:
#TODO: Required fields are missing: [mbfc__Category__c, mbfc__Affiliation__c] 
#TODO: INVALID_TYPE_ON_FIELD_IN_RECORD: Archdiocesan Assignment: value not of required type:  [ADPDX_Archdiocesan_Assignment__c]


In [ ]:
# Set Archdpdx_Migration_Id__c External ID
df_affiliations['Archdpdx_Migration_Id__c'] = df_affiliations.index

# Create Job ID
df_affiliations['Archdpdx_Job_Id__c'] = curr_job_id



In [ ]:
# Final cleanup
df_affiliations.drop(columns=['Account_Ext_Id'], inplace=True)

#FIXME: INVALID_FIELD: Foreign key external ID: relcommunities_23 not found for field Archdpdx_Migration_Id__c
#FIXME: INVALID_FIELD: Foreign key external ID: offices_0 not found for field Archdpdx_Migration_Id__c
#FIXME: Record #115 > FIELD_INTEGRITY_EXCEPTION: Start Date: invalid date: Tue Aug 01 00:00:00 GMT 1021 [mbfc__Start_Date__c

In [ ]:
df_affiliations.to_csv('staging_files/affiliations_staging.csv', encoding='utf-8', index=False)

In [ ]:
# @title Upsert Register Entry Records

bulk_data = []
for row in df_affiliations.itertuples(index=False):
    d = row._asdict()
    bulk_data.append(d)

In [ ]:
# Attempt to use s-s's bulk 2.0 api
# with open('staging_files/affiliations_staging.csv', 'r', encoding='utf-8') as file:
#     csv_data = file.read()


# affiliation_upsert = sf.bulk2.mbfc__Placement__c.upsert('staging_files/affiliations_staging.csv', external_id_field='Archdpdx_Migration_Id__c', encode='utf-8')

In [ ]:
# Upsert Salesforce records
# FIXME: Encoding is getting messed up and I'm unsure how to pass in a parameter that will fix this. 
affiliation_upsert = sf.bulk.mbfc__Placement__c.upsert(data=bulk_data, external_id_field='Archdpdx_Migration_Id__c', batch_size=1000, use_serial=False)
affiliation_upsert_results = pd.DataFrame(affiliation_upsert)

affiliation_upsert_results

success  created    id  \
0       False    False  None   
1       False    False  None   
2       False     True  None   
3       False    False  None   
4       False    False  None   
...       ...      ...   ...   
7795    False    False  None   
7796    False     True  None   
7797    False    False  None   
7798    False    False  None   
7799    False     True  None   

                                                 errors  
0     [{'statusCode': 'INVALID_FIELD', 'message': 'U...  
1     [{'statusCode': 'INVALID_FIELD', 'message': 'J...  
2     [{'statusCode': 'FIELD_CUSTOM_VALIDATION_EXCEP...  
3     [{'statusCode': 'INVALID_FIELD', 'message': 'J...  
4     [{'statusCode': 'INVALID_FIELD', 'message': 'J...  
...                                                 ...  
7795  [{'statusCode': 'INVALID_FIELD', 'message': 'J...  
7796  [{'statusCode': 'FIELD_CUSTOM_VALIDATION_EXCEP...  
7797  [{'statusCode': 'INVALID_FIELD', 'message': 'J...  
7798  [{'statusCode': 'INVALID_FIELD', 'message': 'J...  
7799  [{'statusCode': 'FIELD_CUSTOM_VALIDATION_EXCEP...  

[7800 rows x 4 columns]

In [ ]:
affiliation_upsert_results.to_csv('results_files/affiliation_upsert_results')


# Post-Migration Manual Updates

1. Convert 'Offices' that are ADPDX Pastoral Centre offices into record type: 'Groups', and set their parentID to the Diocese (there are just 6 of these accounts).
1. Update the Religous Order records 'Religious Superior' lookup.
1. Set 'organization type' field value for each account in the 'organization' load: Offices, Newman Centres, Schools, Organizations
1. Consolidate education degree titles in 'Affiliation.Affiliation' picklist into the standard value
